# Running scVI on all donors data (sn + sc):

All cells manifold

Correcting by `sample`

In [1]:
from __future__ import print_function
import torch

In [2]:
import sys, os
data_type = 'float32'
os.environ["THEANO_FLAGS"] = 'device=cuda,floatX=' + data_type + ',force_device=True'
#sys.path.insert(1, '/nfs/team292/aa22/scVI_related/202105_troph_organoids/')

**Set up scVI environment**

In [3]:
import scvi
import scanpy as sc

sc.set_figure_params(figsize=(4, 4))

In [4]:
import pandas as pd 
import numpy as np

**Read in raw counts of the all donors object**

In [5]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [6]:
# reading IDs of final cells to keep (after also excluding doublets by GEX, done in notebook M3)
nodoublet_IDs = pd.read_csv(save_path + 'selected_droplets_no_doublets_in_M1_prelim_analysis.csv', index_col=0)
nodoublet_IDs

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AAACGGGCATTGGCGC-1_FCA7167219           1941        FCA7167219   
AAACGGGTCGCGATCG-1_FCA7167219           1246        FCA7167219   
AAAGATGAGCAATATG-1_FCA7167219           1516        FCA7167219   
AAAGATGAGTTCGCGC-1_FCA7167219           2099        FCA7167219   
AAAGATGCATGTCGAT-1_FCA7167219           1636        FCA7167219   
...                                      ...               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920     2409  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920     3116  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AAACGGGCATTGGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAACGGGTCGCGATCG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGCAATATG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGTTCGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGCATGTCGAT-1_FCA7167219        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AAACGGGCATTGGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAACGGGTCGCGATCG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGCAATATG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGTTCGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGCATGTCGAT-1_FCA7167219                     decidua_immune   13_PCW   
...                                                          ...      ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AAACGGGCATTGGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAACGGGTCGCGATCG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGCAATATG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGTTCGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGCATGTCGAT-1_FCA7167219           6          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AAACGGGCATTGGCGC-1_FCA7167219                                        1      0   
AAACGGGTCGCGATCG-1_FCA7167219                                        1      0   
AAAGATGAGCAATATG-1_FCA7167219                                        1      0   
AAAGATGAGTTCGCGC-1_FCA7167219                                        1      0   
AAAGATGCATG

In [7]:
# subsetting the adata object to final cells
adata = adata[list(nodoublet_IDs.index), :].copy()
adata

AnnData object with n_obs × n_vars = 378558 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feature_types-1

In [8]:
# adding metadata
for col in nodoublet_IDs.columns:
    print(col)
    adata.obs[col] = nodoublet_IDs.loc[adata.obs_names,col]

n_genes
sample
technology
tissue
dev_age
donor
dataset
run
number_of_individuals_multiplexed
batch
percent_mito
n_counts
scrublet_score
scrublet_cluster_score
bh_pval
is_doublet
celltype_predictions
probabilities
barcode_sample_copy
souporcell_assignment
inter_ind_doublet
S_score
G2M_score
phase
origin_M_F
is_doublet_0.05
is_doublet_0.01


In [9]:
# addition - subsetting to genes after cell cycle-associated gene removal (notebook M3)
# read in cleaned up genes, after all doublet exclusion
cleaned_up_genes = pd.read_csv(save_path + 'cleaned_up_genes_in_M2_notebook_all_cells_and_nuclei_20211111.csv', 
                              index_col=0)
cleaned_up_genes

gene_ids-0  feature_types-0 genome-0  n_cells-0  \
A1BG      ENSG00000121410  Gene Expression   GRCh38       58.0   
A1BG-AS1  ENSG00000268895  Gene Expression   GRCh38        7.0   
A1CF                  NaN              NaN      NaN        NaN   
A2M       ENSG00000175899  Gene Expression   GRCh38       66.0   
A2M-AS1   ENSG00000245105  Gene Expression   GRCh38        6.0   
...                   ...              ...      ...        ...   
ZXDC      ENSG00000070476  Gene Expression   GRCh38       11.0   
ZYG11A                NaN              NaN      NaN        NaN   
ZYG11B    ENSG00000162378  Gene Expression   GRCh38       15.0   
ZYX       ENSG00000159840  Gene Expression   GRCh38      134.0   
ZZEF1     ENSG00000074755  Gene Expression   GRCh38       41.0   

               gene_ids-1  feature_types-1 genome-1  n_cells-1  \
A1BG      ENSG00000121410  Gene Expression   GRCh38      118.0   
A1BG-AS1  ENSG00000268895  Gene Expression   GRCh38       21.0   
A1CF                  NaN              NaN      NaN        NaN   
A2M       ENSG00000175899  Gene Expression   GRCh38      171.0   
A2M-AS1   ENSG00000245105  Gene Expression   GRCh38        5.0   
...                   ...              ...      ...        ...   
ZXDC      ENSG00000070476  Gene Expression   GRCh38       21.0   
ZYG11A                NaN              NaN      NaN        NaN   
ZYG11B    ENSG00000162378  Gene Expression   GRCh38       41.0   
ZYX       ENSG00000159840  Gene Expression   GRCh38      284.0   
ZZEF1     ENSG00000074755  Gene Expression   GRCh38       88.0   

              gene_ids-10 feature_types-10  ... genome-7  n_cells-7  \
A1BG      ENSG00000121410  Gene Expression  ...   GRCh38      140.0   
A1BG-AS1  ENSG00000268895  Gene Expression  ...   GRCh38       14.0   
A1CF                  NaN              NaN  ...      NaN        NaN   
A2M       ENSG00000175899  Gene Expression  ...      NaN        NaN   
A2M-AS1   ENSG00000245105  Gene Expression  ...   GRCh38       59.0   
...                   ...              ...  ...      ...        ...   
ZXDC      ENSG00000070476  Gene Expression  ...   GRCh38       26.0   
ZYG11A                NaN              NaN  ...      NaN        NaN   
ZYG11B    ENSG00000162378  Gene Expression  ...   GRCh38       22.0   
ZYX       ENSG00000159840  Gene Expression  ...   GRCh38      265.0   
ZZEF1     ENSG00000074755  Gene Expression  ...   GRCh38       58.0   

               gene_ids-8  feature_types-8 genome-8  n_cells-8  \
A1BG      ENSG00000121410  Gene Expression   GRCh38      185.0   
A1BG-AS1  ENSG00000268895  Gene Expression   GRCh38       20.0   
A1CF                  NaN              NaN      NaN        NaN   
A2M       ENSG00000175899  Gene Expression   GRCh38        5.0   
A2M-AS1   ENSG00000245105  Gene Expression   GRCh38       61.0   
...                   ...              ...      ...        ...   
ZXDC      ENSG00000070476  Gene Expression   GRCh38       32.0   
ZYG11A                NaN              NaN      NaN        NaN   
ZYG11B    ENSG00000162378  Gene Expression   GRCh38       47.0   
ZYX       ENSG00000159840  Gene Expression   GRCh38      319.0   
ZZEF1     ENSG00000074755  Gene Expression   GRCh38       46.0   

               gene_ids-9  feature_types-9 genome-9  n_cells-9  
A1BG      ENSG00000121410  Gene Expression   GRCh38      608.0  
A1BG-AS1  ENSG00000268895  Gene Expression   GRCh38       91.0  
A1CF                  NaN              NaN      NaN        NaN  
A2M       ENSG00000175899  Gene Expression   GRCh38     2117.0  
A2M-AS1   ENSG00000245105  Gene Expression   GRCh38       13.0  
...                   ...              ...      ...        ...  
ZXDC      ENSG00000070476  Gene Expression   GRCh38      122.0  
ZYG11A                NaN              NaN      NaN        NaN  
ZYG11B    ENSG00000162378  Gene Expression   GRCh38      183.0  
ZYX       ENSG00000159840  Gene Expression   GRCh38     2351.0  
ZZEF1     ENSG00000074755  Gene Expression   GRCh38      299.0  

[3

In [10]:
# subsetting to only cleamed up genes
adata = adata[:, list(cleaned_up_genes.index)].copy()

In [11]:
adata

AnnData object with n_obs × n_vars = 378558 × 30721
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'featur

In [12]:
# going to correct by sample here
np.unique(adata.obs['sample'], return_counts=True)

(array(['FCA7167219', 'FCA7167221', 'FCA7167222', 'FCA7167223',
        'FCA7167224', 'FCA7167226', 'FCA7167230', 'FCA7167231',
        'FCA7167232', 'FCA7196218', 'FCA7196219', 'FCA7196220',
        'FCA7196224', 'FCA7196225', 'FCA7196226', 'FCA7196229',
        'FCA7196231', 'FCA7474062', 'FCA7474063', 'FCA7474064',
        'FCA7474065', 'FCA7474066', 'FCA7474068', 'FCA7474069',
        'FCA7511881', 'FCA7511882', 'FCA7511883', 'FCA7511884',
        'FCA7511885', 'FCA7511886', 'Pla_Camb10691970', 'Pla_Camb10691971',
        'Pla_Camb10691972', 'Pla_Camb10691975', 'Pla_Camb10714918',
        'Pla_Camb10714919', 'Pla_Camb10714920', 'Pla_HDBR10142767',
        'Pla_HDBR10142768', 'Pla_HDBR10142769', 'Pla_HDBR10142770',
        'Pla_HDBR10142863', 'Pla_HDBR10142864', 'Pla_HDBR10142865',
        'Pla_HDBR10701666', 'Pla_HDBR10701667', 'Pla_HDBR10701668',
        'Pla_HDBR10917730', 'Pla_HDBR10917731', 'Pla_HDBR10917733',
        'Pla_HDBR8624430', 'Pla_HDBR8624431', 'Pla_HDBR8715512',
   

In [13]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [14]:
# creating a joint donor + sample key for the most correct HVG calculation in case of donor + sample correction
#adata.obs['donor_sample'] = [i + '_' + j for i,j in zip(adata.obs['donor'], adata.obs['sample'])]

In [15]:
# here we subset to HVGs, accounting for donor batch
sc.pp.highly_variable_genes(
    adata,
    n_top_genes=2000,
    subset=True,
    #layer="raw_counts",
    flavor="seurat",
    batch_key="sample",
    #batch_key="donor"
)

... storing 'sample' as categorical
... storing 'technology' as categorical
... storing 'tissue' as categorical
... storing 'dev_age' as categorical
... storing 'dataset' as categorical
... storing 'celltype_predictions' as categorical
... storing 'souporcell_assignment' as categorical
... storing 'phase' as categorical
... storing 'origin_M_F' as categorical
/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/pandas/core/indexing.py:1637: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_block(indexer, value, name)


In [16]:
adata

AnnData object with n_obs × n_vars = 378558 × 2000
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature

#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [17]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 378558 cells, 2000 vars, 1        
         batches, 1 labels, and 0 proteins. Also registered 1 extra categorical covariates   
         and 0 extra continuous covariates.                                                  
INFO     Please do not further modify adata until model is trained.                          


### 11.11.2021 Running scVI after:

- removing cell cycle-associated genes (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell, notebook M1)

this worked worse than the same run + removing soupy genes (see next bit of code)

In [19]:
# as this is a particularly challenging integration, trying to play with n_layers here
# more layers in the model may help integrate data better
models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

n_latent_values = [16]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 16


In [20]:
models_n_layers_1[16]

SCVI Model with the following params: 
n_hidden: 128, n_latent: 16, n_layers: 1, dropout_rate: 0.1, dispersion: gene, 
gene_likelihood: zinb, latent_distribution: normal
Training status: Not Trained

To print summary of associated AnnData, use: scvi.data.view_anndata_setup(model.adata)

In [21]:
models_n_layers_2[16]

SCVI Model with the following params: 
n_hidden: 128, n_latent: 16, n_layers: 2, dropout_rate: 0.1, dispersion: gene, 
gene_likelihood: zinb, latent_distribution: normal
Training status: Not Trained

To print summary of associated AnnData, use: scvi.data.view_anndata_setup(model.adata)

In [22]:
models_n_layers_3[16]

SCVI Model with the following params: 
n_hidden: 128, n_latent: 16, n_layers: 3, dropout_rate: 0.1, dispersion: gene, 
gene_likelihood: zinb, latent_distribution: normal
Training status: Not Trained

To print summary of associated AnnData, use: scvi.data.view_anndata_setup(model.adata)

In [23]:
latent_representations_n_layers_1 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_1[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_1[n_latent_value] = models_n_layers_1[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_1"] = latent_representations_n_layers_1[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_1"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211111_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_CCG_removal_and_all_doublet_exclusion_by_sample_all_cells_and_nuclei_n_layers_1.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 16
Epoch 21/21: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 21/21 [07:10<00:00, 20.51s/it, loss=782, v_num=1]


In [24]:
latent_representations_n_layers_2 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_2[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_2[n_latent_value] = models_n_layers_2[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_2"] = latent_representations_n_layers_2[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_2"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211111_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_CCG_removal_and_all_doublet_exclusion_by_sample_all_cells_and_nuclei_n_layers_2.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 16
Epoch 21/21: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 21/21 [08:15<00:00, 23.58s/it, loss=794, v_num=1]


In [25]:
latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211111_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_CCG_removal_and_all_doublet_exclusion_by_sample_all_cells_and_nuclei_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 16
Epoch 21/21: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 21/21 [09:15<00:00, 26.46s/it, loss=787, v_num=1]


# Running on all cells and nuclei with soupy gene filtering


## This is what I end up using

In [5]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [7]:
# reading IDs of final cells to keep (after also excluding doublets by GEX, done in notebook M3)
nodoublet_cell_IDs = pd.read_csv(save_path + 'selected_droplets_no_doublets_in_M1_prelim_analysis.csv', index_col=0)
nodoublet_cell_IDs

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AAACGGGCATTGGCGC-1_FCA7167219           1941        FCA7167219   
AAACGGGTCGCGATCG-1_FCA7167219           1246        FCA7167219   
AAAGATGAGCAATATG-1_FCA7167219           1516        FCA7167219   
AAAGATGAGTTCGCGC-1_FCA7167219           2099        FCA7167219   
AAAGATGCATGTCGAT-1_FCA7167219           1636        FCA7167219   
...                                      ...               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920     2409  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920     3116  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AAACGGGCATTGGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAACGGGTCGCGATCG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGCAATATG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGTTCGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGCATGTCGAT-1_FCA7167219        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AAACGGGCATTGGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAACGGGTCGCGATCG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGCAATATG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGTTCGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGCATGTCGAT-1_FCA7167219                     decidua_immune   13_PCW   
...                                                          ...      ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AAACGGGCATTGGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAACGGGTCGCGATCG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGCAATATG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGTTCGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGCATGTCGAT-1_FCA7167219           6          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AAACGGGCATTGGCGC-1_FCA7167219                                        1      0   
AAACGGGTCGCGATCG-1_FCA7167219                                        1      0   
AAAGATGAGCAATATG-1_FCA7167219                                        1      0   
AAAGATGAGTTCGCGC-1_FCA7167219                                        1      0   
AAAGATGCATG

In [8]:
# subsetting the adata object to final cells
adata = adata[list(nodoublet_cell_IDs.index), :].copy()
adata

AnnData object with n_obs × n_vars = 378558 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feature_types-1

In [9]:
# adding metadata
for col in nodoublet_cell_IDs.columns:
    print(col)
    adata.obs[col] = nodoublet_cell_IDs.loc[adata.obs_names,col]

n_genes
sample
technology
tissue
dev_age
donor
dataset
run
number_of_individuals_multiplexed
batch
percent_mito
n_counts
scrublet_score
scrublet_cluster_score
bh_pval
is_doublet
celltype_predictions
probabilities
barcode_sample_copy
souporcell_assignment
inter_ind_doublet
S_score
G2M_score
phase
origin_M_F
is_doublet_0.05
is_doublet_0.01


In [10]:
# excluding soupy genes as per notebook M2

# gene stats for cells
gene_stats_sc = pd.read_csv(save_path + 'gene_filter_cells_upd_20211111.csv', index_col=0)

# gene stats for nuclei
gene_stats_sn = pd.read_csv(save_path + 'gene_filter_nuclei_upd_20211111.csv', index_col=0)

genes2keep_sc = list(gene_stats_sc[gene_stats_sc['Selected'] == True].index)
genes2keep_sn = list(gene_stats_sn[gene_stats_sn['Selected'] == True].index)

# overlap
genes2keep = list(set(genes2keep_sc) & set(genes2keep_sn))

print(len(genes2keep))

adata = adata[:,list(set(genes2keep) & set(adata.var_names))].copy()
adata

# cell cycle related - no need to, seems like all of those have been removed by soupy gene filter
#cleaned_up_genes_cc = pd.read_csv(save_path + '', index_col=0)

7849


AnnData object with n_obs × n_vars = 378558 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature

In [11]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [12]:
# here we subset to HVGs, accounting for donor batch
sc.pp.highly_variable_genes(
    adata,
    n_top_genes=2000,
    subset=True,
    #layer="raw_counts",
    flavor="seurat",
    batch_key="sample",
    #batch_key="donor"
)

... storing 'sample' as categorical
... storing 'technology' as categorical
... storing 'tissue' as categorical
... storing 'dev_age' as categorical
... storing 'dataset' as categorical
... storing 'celltype_predictions' as categorical
... storing 'souporcell_assignment' as categorical
... storing 'phase' as categorical
... storing 'origin_M_F' as categorical
/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/pandas/core/indexing.py:1637: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_block(indexer, value, name)


#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [13]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 378558 cells, 2000 vars, 1        
         batches, 1 labels, and 0 proteins. Also registered 1 extra categorical covariates   
         and 0 extra continuous covariates.                                                  
INFO     Please do not further modify adata until model is trained.                          


### 11.11.2021 Running scVI after:

- removing soupy genes (calculated in notebook M2)
- exclusion of all doublets (scrublet and souporcell, notebook M1)


In [14]:
models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

n_latent_values = [16]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 16


In [15]:
models_n_layers_1[16]

SCVI Model with the following params: 
n_hidden: 128, n_latent: 16, n_layers: 1, dropout_rate: 0.1, dispersion: gene, 
gene_likelihood: zinb, latent_distribution: normal
Training status: Not Trained

To print summary of associated AnnData, use: scvi.data.view_anndata_setup(model.adata)

In [16]:
models_n_layers_2[16]

SCVI Model with the following params: 
n_hidden: 128, n_latent: 16, n_layers: 2, dropout_rate: 0.1, dispersion: gene, 
gene_likelihood: zinb, latent_distribution: normal
Training status: Not Trained

To print summary of associated AnnData, use: scvi.data.view_anndata_setup(model.adata)

In [17]:
models_n_layers_3[16]

SCVI Model with the following params: 
n_hidden: 128, n_latent: 16, n_layers: 3, dropout_rate: 0.1, dispersion: gene, 
gene_likelihood: zinb, latent_distribution: normal
Training status: Not Trained

To print summary of associated AnnData, use: scvi.data.view_anndata_setup(model.adata)

In [18]:
latent_representations_n_layers_1 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_1[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_1[n_latent_value] = models_n_layers_1[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_1"] = latent_representations_n_layers_1[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_1"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211111_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_CCG_removal_and_all_doublet_exclusion_by_sample_all_cells_and_nuclei_with_LF_gene_filter_n_layers_1.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 16
Epoch 21/21: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 21/21 [07:12<00:00, 20.59s/it, loss=718, v_num=1]


In [19]:
latent_representations_n_layers_2 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_2[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_2[n_latent_value] = models_n_layers_2[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_2"] = latent_representations_n_layers_2[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_2"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211111_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_CCG_removal_and_all_doublet_exclusion_by_sample_all_cells_and_nuclei_with_LF_gene_filter_n_layers_2.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 16
Epoch 21/21: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 21/21 [08:13<00:00, 23.49s/it, loss=710, v_num=1]


In [20]:
latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211111_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_CCG_removal_and_all_doublet_exclusion_by_sample_all_cells_and_nuclei_with_LF_gene_filter_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 16
Epoch 21/21: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 21/21 [09:11<00:00, 26.24s/it, loss=706, v_num=1]


# Running on only trophoblast 


Subsetted by unbiased clusteing of the manifold with all cell states as calculated above

In [26]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [27]:
# reading IDs of final cells to keep (after also excluding doublets by GEX, done in notebook M3)
nodoublet_cell_IDs = pd.read_csv(save_path + 'selected_droplets_no_doublets_in_M1_prelim_analysis.csv', index_col=0)
nodoublet_cell_IDs

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AAACGGGCATTGGCGC-1_FCA7167219           1941        FCA7167219   
AAACGGGTCGCGATCG-1_FCA7167219           1246        FCA7167219   
AAAGATGAGCAATATG-1_FCA7167219           1516        FCA7167219   
AAAGATGAGTTCGCGC-1_FCA7167219           2099        FCA7167219   
AAAGATGCATGTCGAT-1_FCA7167219           1636        FCA7167219   
...                                      ...               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920     2409  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920     3116  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AAACGGGCATTGGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAACGGGTCGCGATCG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGCAATATG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGTTCGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGCATGTCGAT-1_FCA7167219        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AAACGGGCATTGGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAACGGGTCGCGATCG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGCAATATG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGTTCGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGCATGTCGAT-1_FCA7167219                     decidua_immune   13_PCW   
...                                                          ...      ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AAACGGGCATTGGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAACGGGTCGCGATCG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGCAATATG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGTTCGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGCATGTCGAT-1_FCA7167219           6          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AAACGGGCATTGGCGC-1_FCA7167219                                        1      0   
AAACGGGTCGCGATCG-1_FCA7167219                                        1      0   
AAAGATGAGCAATATG-1_FCA7167219                                        1      0   
AAAGATGAGTTCGCGC-1_FCA7167219                                        1      0   
AAAGATGCATG

In [28]:
# subsetting the adata object to final cells
adata = adata[list(nodoublet_cell_IDs.index), :].copy()
adata

AnnData object with n_obs × n_vars = 378558 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feature_types-1

In [29]:
# adding metadata
for col in nodoublet_cell_IDs.columns:
    print(col)
    adata.obs[col] = nodoublet_cell_IDs.loc[adata.obs_names,col]

n_genes
sample
technology
tissue
dev_age
donor
dataset
run
number_of_individuals_multiplexed
batch
percent_mito
n_counts
scrublet_score
scrublet_cluster_score
bh_pval
is_doublet
celltype_predictions
probabilities
barcode_sample_copy
souporcell_assignment
inter_ind_doublet
S_score
G2M_score
phase
origin_M_F
is_doublet_0.05
is_doublet_0.01


In [30]:
# excluding soupy genes as per notebook M3a-1

# gene stats for cells
gene_stats_sc = pd.read_csv(save_path + 'gene_filter_cells_upd_20211111.csv', index_col=0)

# gene stats for nuclei
gene_stats_sn = pd.read_csv(save_path + 'gene_filter_nuclei_upd_20211111.csv', index_col=0)

genes2keep_sc = list(gene_stats_sc[gene_stats_sc['Selected'] == True].index)
genes2keep_sn = list(gene_stats_sn[gene_stats_sn['Selected'] == True].index)

# overlap
genes2keep = list(set(genes2keep_sc) & set(genes2keep_sn))

print(len(genes2keep))

adata = adata[:,list(set(genes2keep) & set(adata.var_names))].copy()
adata

# cell cycle related - no need to, seems like all of those have been removed by soupy gene filter
#cleaned_up_genes_cc = pd.read_csv(save_path + '', index_col=0)

7849


AnnData object with n_obs × n_vars = 378558 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature

In [31]:
# subsetting to only trophoblast according to coarse annotation done in notebook M4
annot_coarse = pd.read_csv(save_path + 'obs_table_with_coarse_annot_from_M4_notebook_all_cell_states.csv',
                          index_col=0)
adata.obs['annot_coarse'] = annot_coarse.loc[adata.obs_names,'annot_coarse']
adata.obs['annot_coarse'].value_counts()

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6,28) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


dS_uSMC        158106
Trophoblast     81704
Myeloid         43997
NK              30132
T               19244
Epithelial      18222
Endothelial     12689
fF              12633
PV               1831
Name: annot_coarse, dtype: int64

In [32]:
adata = adata[adata.obs['annot_coarse'] == 'Trophoblast'].copy()

In [33]:
adata

AnnData object with n_obs × n_vars = 81704 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_id

In [34]:
# no CC-assoc gene filtering here

# optimal n_PCs = 6 here

In [35]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [36]:
adata

AnnData object with n_obs × n_vars = 81704 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_id

In [54]:
# here we subset to HVGs, not accounting for sample batch here - it breaks the HVG finding (not enough batch representation?)
sc.pp.highly_variable_genes(adata, min_mean=0.0125, max_mean=3, min_disp=0.5,
                           subset=True)

In [56]:
adata

AnnData object with n_obs × n_vars = 81704 × 1869
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse', '_scvi_batch', '_scvi_labels', '_scvi_local_l_mean', '_scvi_local_l_var'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-1

#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [58]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 81704 cells, 1869 vars, 1 batches,
         1 labels, and 0 proteins. Also registered 1 extra categorical covariates and 0 extra
         continuous covariates.                                                              
INFO     Please do not further modify adata until model is trained.                          


### 14.11.2021 Running scVI after:

- removing soupy genes as per LF approach (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell)

In [59]:
models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

n_latent_values = [6]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 6


In [60]:
models_n_layers_1[6]

SCVI Model with the following params: 
n_hidden: 128, n_latent: 6, n_layers: 1, dropout_rate: 0.1, dispersion: gene, 
gene_likelihood: zinb, latent_distribution: normal
Training status: Not Trained

To print summary of associated AnnData, use: scvi.data.view_anndata_setup(model.adata)

In [61]:
models_n_layers_2[6]

SCVI Model with the following params: 
n_hidden: 128, n_latent: 6, n_layers: 2, dropout_rate: 0.1, dispersion: gene, 
gene_likelihood: zinb, latent_distribution: normal
Training status: Not Trained

To print summary of associated AnnData, use: scvi.data.view_anndata_setup(model.adata)

In [62]:
models_n_layers_3[6]

SCVI Model with the following params: 
n_hidden: 128, n_latent: 6, n_layers: 3, dropout_rate: 0.1, dispersion: gene, 
gene_likelihood: zinb, latent_distribution: normal
Training status: Not Trained

To print summary of associated AnnData, use: scvi.data.view_anndata_setup(model.adata)

In [63]:
latent_representations_n_layers_1 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_1[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_1[n_latent_value] = models_n_layers_1[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_1"] = latent_representations_n_layers_1[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_1"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_Trophoblast_compartment_with_LF_gene_filter_n_layers_1.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 6
Epoch 98/98: 100%|█████████████████████████████████████████████████████████████████████| 98/98 [07:07<00:00,  4.36s/it, loss=719, v_num=1]


In [64]:
latent_representations_n_layers_2 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_2[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_2[n_latent_value] = models_n_layers_2[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_2"] = latent_representations_n_layers_2[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_2"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_Trophoblast_compartment_with_LF_gene_filter_n_layers_2.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 6
Epoch 98/98: 100%|█████████████████████████████████████████████████████████████████████| 98/98 [08:07<00:00,  4.98s/it, loss=695, v_num=1]


In [65]:
latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_Trophoblast_compartment_with_LF_gene_filter_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 6
Epoch 98/98: 100%|█████████████████████████████████████████████████████████████████████| 98/98 [09:05<00:00,  5.56s/it, loss=713, v_num=1]


# Running on only trophoblast, cleanup (towards v2)


Subsetted by unbiased clusteing of the manifold with all cell states as calculated above

In [5]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [6]:
# reading IDs of final cells to keep (after also excluding doublets by GEX, done in notebook M3)
nodoublet_cell_IDs = pd.read_csv(save_path + 'selected_droplets_no_doublets_in_M1_prelim_analysis.csv', index_col=0)
nodoublet_cell_IDs

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AAACGGGCATTGGCGC-1_FCA7167219           1941        FCA7167219   
AAACGGGTCGCGATCG-1_FCA7167219           1246        FCA7167219   
AAAGATGAGCAATATG-1_FCA7167219           1516        FCA7167219   
AAAGATGAGTTCGCGC-1_FCA7167219           2099        FCA7167219   
AAAGATGCATGTCGAT-1_FCA7167219           1636        FCA7167219   
...                                      ...               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920     2409  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920     3116  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AAACGGGCATTGGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAACGGGTCGCGATCG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGCAATATG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGTTCGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGCATGTCGAT-1_FCA7167219        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AAACGGGCATTGGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAACGGGTCGCGATCG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGCAATATG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGTTCGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGCATGTCGAT-1_FCA7167219                     decidua_immune   13_PCW   
...                                                          ...      ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AAACGGGCATTGGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAACGGGTCGCGATCG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGCAATATG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGTTCGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGCATGTCGAT-1_FCA7167219           6          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AAACGGGCATTGGCGC-1_FCA7167219                                        1      0   
AAACGGGTCGCGATCG-1_FCA7167219                                        1      0   
AAAGATGAGCAATATG-1_FCA7167219                                        1      0   
AAAGATGAGTTCGCGC-1_FCA7167219                                        1      0   
AAAGATGCATG

In [7]:
# subsetting the adata object to final cells
adata = adata[list(nodoublet_cell_IDs.index), :].copy()
adata

AnnData object with n_obs × n_vars = 378558 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feature_types-1

In [8]:
# adding metadata
for col in nodoublet_cell_IDs.columns:
    print(col)
    adata.obs[col] = nodoublet_cell_IDs.loc[adata.obs_names,col]

n_genes
sample
technology
tissue
dev_age
donor
dataset
run
number_of_individuals_multiplexed
batch
percent_mito
n_counts
scrublet_score
scrublet_cluster_score
bh_pval
is_doublet
celltype_predictions
probabilities
barcode_sample_copy
souporcell_assignment
inter_ind_doublet
S_score
G2M_score
phase
origin_M_F
is_doublet_0.05
is_doublet_0.01


In [9]:
# excluding soupy genes as per notebook M3a-1

# gene stats for cells
gene_stats_sc = pd.read_csv(save_path + 'gene_filter_cells_upd_20211111.csv', index_col=0)

# gene stats for nuclei
gene_stats_sn = pd.read_csv(save_path + 'gene_filter_nuclei_upd_20211111.csv', index_col=0)

genes2keep_sc = list(gene_stats_sc[gene_stats_sc['Selected'] == True].index)
genes2keep_sn = list(gene_stats_sn[gene_stats_sn['Selected'] == True].index)

# overlap
genes2keep = list(set(genes2keep_sc) & set(genes2keep_sn))

print(len(genes2keep))

adata = adata[:,list(set(genes2keep) & set(adata.var_names))].copy()
adata

# cell cycle related - no need to, seems like all of those have been removed by soupy gene filter
#cleaned_up_genes_cc = pd.read_csv(save_path + '', index_col=0)

7849


AnnData object with n_obs × n_vars = 378558 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature

In [10]:
# subsetting to only trophoblast according to coarse annotation done in notebook M4
cont_cleanup_1 = pd.read_csv(save_path + 'all_troph_contaminants_cleanup_1.csv',
                          index_col=0)
cont_cleanup_1

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6,29) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AGGGTGAGTAAAGGAG-1_FCA7167219           5291        FCA7167219   
CTGATAGAGCCCAGCT-1_FCA7167219           4070        FCA7167219   
GCGCGATAGATATGGT-1_FCA7167219            506        FCA7167219   
AGGGTGAGTAAAGGAG-1_FCA7167221            819        FCA7167221   
ATTACTCTCTGCGGCA-1_FCA7167221            655        FCA7167221   
...                                      ...               ...   
TTTGTGGCATGGCCTG-1_Pla_Camb10714920     4195  Pla_Camb10714920   
TTTGTGTTCGCTCACT-1_Pla_Camb10714920     1629  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AGGGTGAGTAAAGGAG-1_FCA7167219        10X_3'_scRNA-seq   
CTGATAGAGCCCAGCT-1_FCA7167219        10X_3'_scRNA-seq   
GCGCGATAGATATGGT-1_FCA7167219        10X_3'_scRNA-seq   
AGGGTGAGTAAAGGAG-1_FCA7167221        10X_3'_scRNA-seq   
ATTACTCTCTGCGGCA-1_FCA7167221        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGGCATGGCCTG-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCGCTCACT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AGGGTGAGTAAAGGAG-1_FCA7167219                     decidua_immune   13_PCW   
CTGATAGAGCCCAGCT-1_FCA7167219                     decidua_immune   13_PCW   
GCGCGATAGATATGGT-1_FCA7167219                     decidua_immune   13_PCW   
AGGGTGAGTAAAGGAG-1_FCA7167221                     decidua_immune   11_PCW   
ATTACTCTCTGCGGCA-1_FCA7167221                     decidua_immune   11_PCW   
...                                                          ...      ...   
TTTGTGGCATGGCCTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCGCTCACT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AGGGTGAGTAAAGGAG-1_FCA7167219           6          Vento_Nature  NaN   
CTGATAGAGCCCAGCT-1_FCA7167219           6          Vento_Nature  NaN   
GCGCGATAGATATGGT-1_FCA7167219           6          Vento_Nature  NaN   
AGGGTGAGTAAAGGAG-1_FCA7167221           7          Vento_Nature  NaN   
ATTACTCTCTGCGGCA-1_FCA7167221           7          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGGCATGGCCTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCGCTCACT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AGGGTGAGTAAAGGAG-1_FCA7167219                                        1      0   
CTGATAGAGCCCAGCT-1_FCA7167219                                        1      0   
GCGCGATAGATATGGT-1_FCA7167219                                        1      0   
AGGGTGAGTAAAGGAG-1_FCA7167221                                        1      1   
ATTACTCTCTG

In [14]:
# subset to only troph
adata = adata[cont_cleanup_1.index,:].copy()
adata.obs['troph_contaminants_or_rest_cleanup_1'] = cont_cleanup_1.loc[list(adata.obs_names),'troph_contaminants_or_rest_cleanup_1']
adata.obs['troph_contaminants_or_rest_cleanup_1'].value_counts()


keeping        76993
contaminant     4711
Name: troph_contaminants_or_rest_cleanup_1, dtype: int64

In [15]:
# remove contaminants after cleanup 1 in S0-1 notebook
adata = adata[adata.obs['troph_contaminants_or_rest_cleanup_1'] == 'keeping'].copy()

In [16]:
adata

AnnData object with n_obs × n_vars = 76993 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'troph_contaminants_or_rest_cleanup_1'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15'

In [17]:
# no CC-assoc gene filtering here

# optimal n_PCs = 5 here

In [18]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [19]:
adata

AnnData object with n_obs × n_vars = 76993 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'troph_contaminants_or_rest_cleanup_1'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15'

In [20]:
# here we subset to HVGs, not accounting for sample batch here - it breaks the HVG finding (not enough batch representation?)
sc.pp.highly_variable_genes(adata, min_mean=0.0125, max_mean=3, min_disp=0.5,
                           subset=True)

In [21]:
adata

AnnData object with n_obs × n_vars = 76993 × 1897
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'troph_contaminants_or_rest_cleanup_1'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15'

#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [22]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 76993 cells, 1897 vars, 1 batches,
         1 labels, and 0 proteins. Also registered 1 extra categorical covariates and 0 extra
         continuous covariates.                                                              
INFO     Please do not further modify adata until model is trained.                          


### 14.11.2021 Running scVI after:

- removing soupy genes as per LF approach (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell)

In [24]:
models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

n_latent_values = [5]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 5


In [25]:
models_n_layers_1[5]

SCVI Model with the following params: 
n_hidden: 128, n_latent: 5, n_layers: 1, dropout_rate: 0.1, dispersion: gene, 
gene_likelihood: zinb, latent_distribution: normal
Training status: Not Trained

To print summary of associated AnnData, use: scvi.data.view_anndata_setup(model.adata)

In [26]:
models_n_layers_2[5]

SCVI Model with the following params: 
n_hidden: 128, n_latent: 5, n_layers: 2, dropout_rate: 0.1, dispersion: gene, 
gene_likelihood: zinb, latent_distribution: normal
Training status: Not Trained

To print summary of associated AnnData, use: scvi.data.view_anndata_setup(model.adata)

In [27]:
models_n_layers_3[5]

SCVI Model with the following params: 
n_hidden: 128, n_latent: 5, n_layers: 3, dropout_rate: 0.1, dispersion: gene, 
gene_likelihood: zinb, latent_distribution: normal
Training status: Not Trained

To print summary of associated AnnData, use: scvi.data.view_anndata_setup(model.adata)

In [28]:
latent_representations_n_layers_1 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_1[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_1[n_latent_value] = models_n_layers_1[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_1"] = latent_representations_n_layers_1[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_1"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_Trophoblast_compartment_v2_with_LF_gene_filter_n_layers_1.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 5
Epoch 104/104: 100%|██████████████████████████████████████████████████████████████████| 104/104 [07:10<00:00,  4.13s/it, loss=741, v_num=1]


In [29]:
latent_representations_n_layers_2 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_2[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_2[n_latent_value] = models_n_layers_2[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_2"] = latent_representations_n_layers_2[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_2"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_Trophoblast_compartment_v2_with_LF_gene_filter_n_layers_2.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 5
Epoch 104/104: 100%|██████████████████████████████████████████████████████████████████| 104/104 [08:11<00:00,  4.72s/it, loss=742, v_num=1]


In [30]:
latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_Trophoblast_compartment_v2_with_LF_gene_filter_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 5
Epoch 104/104: 100%|██████████████████████████████████████████████████████████████████| 104/104 [09:11<00:00,  5.30s/it, loss=744, v_num=1]


# Running on only invading trophoblast, v1


Subsetted by unbiased clusteing of the manifold with all cell states as calculated above

In [31]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [32]:
# reading IDs of final cells to keep (after also excluding doublets by GEX, done in notebook M3)
nodoublet_cell_IDs = pd.read_csv(save_path + 'selected_droplets_no_doublets_in_M1_prelim_analysis.csv', index_col=0)
nodoublet_cell_IDs

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AAACGGGCATTGGCGC-1_FCA7167219           1941        FCA7167219   
AAACGGGTCGCGATCG-1_FCA7167219           1246        FCA7167219   
AAAGATGAGCAATATG-1_FCA7167219           1516        FCA7167219   
AAAGATGAGTTCGCGC-1_FCA7167219           2099        FCA7167219   
AAAGATGCATGTCGAT-1_FCA7167219           1636        FCA7167219   
...                                      ...               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920     2409  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920     3116  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AAACGGGCATTGGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAACGGGTCGCGATCG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGCAATATG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGTTCGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGCATGTCGAT-1_FCA7167219        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AAACGGGCATTGGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAACGGGTCGCGATCG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGCAATATG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGTTCGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGCATGTCGAT-1_FCA7167219                     decidua_immune   13_PCW   
...                                                          ...      ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AAACGGGCATTGGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAACGGGTCGCGATCG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGCAATATG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGTTCGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGCATGTCGAT-1_FCA7167219           6          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AAACGGGCATTGGCGC-1_FCA7167219                                        1      0   
AAACGGGTCGCGATCG-1_FCA7167219                                        1      0   
AAAGATGAGCAATATG-1_FCA7167219                                        1      0   
AAAGATGAGTTCGCGC-1_FCA7167219                                        1      0   
AAAGATGCATG

In [33]:
# subsetting the adata object to final cells
adata = adata[list(nodoublet_cell_IDs.index), :].copy()
adata

AnnData object with n_obs × n_vars = 378558 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feature_types-1

In [34]:
# adding metadata
for col in nodoublet_cell_IDs.columns:
    print(col)
    adata.obs[col] = nodoublet_cell_IDs.loc[adata.obs_names,col]

n_genes
sample
technology
tissue
dev_age
donor
dataset
run
number_of_individuals_multiplexed
batch
percent_mito
n_counts
scrublet_score
scrublet_cluster_score
bh_pval
is_doublet
celltype_predictions
probabilities
barcode_sample_copy
souporcell_assignment
inter_ind_doublet
S_score
G2M_score
phase
origin_M_F
is_doublet_0.05
is_doublet_0.01


In [35]:
# excluding soupy genes as per notebook M3a-1

# gene stats for cells
gene_stats_sc = pd.read_csv(save_path + 'gene_filter_cells_upd_20211111.csv', index_col=0)

# gene stats for nuclei
gene_stats_sn = pd.read_csv(save_path + 'gene_filter_nuclei_upd_20211111.csv', index_col=0)

genes2keep_sc = list(gene_stats_sc[gene_stats_sc['Selected'] == True].index)
genes2keep_sn = list(gene_stats_sn[gene_stats_sn['Selected'] == True].index)

# overlap
genes2keep = list(set(genes2keep_sc) & set(genes2keep_sn))

print(len(genes2keep))

adata = adata[:,list(set(genes2keep) & set(adata.var_names))].copy()
adata

# cell cycle related - no need to, seems like all of those have been removed by soupy gene filter
#cleaned_up_genes_cc = pd.read_csv(save_path + '', index_col=0)

7849


AnnData object with n_obs × n_vars = 378558 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature

In [36]:
# subsetting to only invading troph as annotated in S0-2 notebook
annot = pd.read_csv(save_path + 'obs_table_all_troph_v2_prelim_annot.csv',
                          index_col=0)
annot

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6,30) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AGGGTGAGTAAAGGAG-1_FCA7167219           5291        FCA7167219   
CTGATAGAGCCCAGCT-1_FCA7167219           4070        FCA7167219   
GCGCGATAGATATGGT-1_FCA7167219            506        FCA7167219   
AGGGTGAGTAAAGGAG-1_FCA7167221            819        FCA7167221   
ATTACTCTCTGCGGCA-1_FCA7167221            655        FCA7167221   
...                                      ...               ...   
TTTGTGGCATGGCCTG-1_Pla_Camb10714920     4195  Pla_Camb10714920   
TTTGTGTTCGCTCACT-1_Pla_Camb10714920     1629  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AGGGTGAGTAAAGGAG-1_FCA7167219        10X_3'_scRNA-seq   
CTGATAGAGCCCAGCT-1_FCA7167219        10X_3'_scRNA-seq   
GCGCGATAGATATGGT-1_FCA7167219        10X_3'_scRNA-seq   
AGGGTGAGTAAAGGAG-1_FCA7167221        10X_3'_scRNA-seq   
ATTACTCTCTGCGGCA-1_FCA7167221        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGGCATGGCCTG-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCGCTCACT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AGGGTGAGTAAAGGAG-1_FCA7167219                     decidua_immune   13_PCW   
CTGATAGAGCCCAGCT-1_FCA7167219                     decidua_immune   13_PCW   
GCGCGATAGATATGGT-1_FCA7167219                     decidua_immune   13_PCW   
AGGGTGAGTAAAGGAG-1_FCA7167221                     decidua_immune   11_PCW   
ATTACTCTCTGCGGCA-1_FCA7167221                     decidua_immune   11_PCW   
...                                                          ...      ...   
TTTGTGGCATGGCCTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCGCTCACT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AGGGTGAGTAAAGGAG-1_FCA7167219           6          Vento_Nature  NaN   
CTGATAGAGCCCAGCT-1_FCA7167219           6          Vento_Nature  NaN   
GCGCGATAGATATGGT-1_FCA7167219           6          Vento_Nature  NaN   
AGGGTGAGTAAAGGAG-1_FCA7167221           7          Vento_Nature  NaN   
ATTACTCTCTGCGGCA-1_FCA7167221           7          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGGCATGGCCTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCGCTCACT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AGGGTGAGTAAAGGAG-1_FCA7167219                                        1      0   
CTGATAGAGCCCAGCT-1_FCA7167219                                        1      0   
GCGCGATAGATATGGT-1_FCA7167219                                        1      0   
AGGGTGAGTAAAGGAG-1_FCA7167221                                        1      1   
ATTACTCTCTG

In [37]:
# subset to only troph
adata = adata[annot.index,:].copy()
adata.obs['inv_troph_or_rest'] = annot.loc[list(adata.obs_names),'prelim_annot']
adata.obs['inv_troph_or_rest'].value_counts()


rest         60532
inv_troph    16461
Name: inv_troph_or_rest, dtype: int64

In [38]:
# remove contaminants after cleanup 1 in S0-1 notebook
adata = adata[adata.obs['inv_troph_or_rest'] == 'inv_troph'].copy()

In [39]:
adata

AnnData object with n_obs × n_vars = 16461 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'inv_troph_or_rest'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'ge

In [40]:
# no CC-assoc gene filtering here

# optimal n_PCs = 6 here

In [41]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [42]:
adata

AnnData object with n_obs × n_vars = 16461 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'inv_troph_or_rest'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'ge

In [43]:
# here we subset to HVGs, not accounting for sample batch here - it breaks the HVG finding (not enough batch representation?)
sc.pp.highly_variable_genes(adata, min_mean=0.0125, max_mean=3, min_disp=0.5,
                           subset=True)

In [44]:
adata

AnnData object with n_obs × n_vars = 16461 × 1774
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'inv_troph_or_rest'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'ge

#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [45]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 16461 cells, 1774 vars, 1 batches,
         1 labels, and 0 proteins. Also registered 1 extra categorical covariates and 0 extra
         continuous covariates.                                                              
INFO     Please do not further modify adata until model is trained.                          


### 14.11.2021 Running scVI after:

- removing soupy genes as per LF approach (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell)

In [47]:
models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

# just a few values here, it was 17 PCs I used in the conventional analysis
n_latent_values = [6]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 6


In [48]:
latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_Trophoblast_compartment_only_inv_troph_v1_with_LF_gene_filter_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 6
Epoch 400/400: 100%|██████████████████████████████████████████████████████████████████| 400/400 [07:27<00:00,  1.12s/it, loss=730, v_num=1]


# Running on only invading trophoblast, v2


Subsetted by unbiased clusteing of the manifold with all cell states as calculated above with n_latent=

In [49]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [50]:
# reading IDs of final cells to keep (after also excluding doublets by GEX, done in notebook M3)
nodoublet_cell_IDs = pd.read_csv(save_path + 'selected_droplets_no_doublets_in_M1_prelim_analysis.csv', index_col=0)
nodoublet_cell_IDs

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AAACGGGCATTGGCGC-1_FCA7167219           1941        FCA7167219   
AAACGGGTCGCGATCG-1_FCA7167219           1246        FCA7167219   
AAAGATGAGCAATATG-1_FCA7167219           1516        FCA7167219   
AAAGATGAGTTCGCGC-1_FCA7167219           2099        FCA7167219   
AAAGATGCATGTCGAT-1_FCA7167219           1636        FCA7167219   
...                                      ...               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920     2409  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920     3116  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AAACGGGCATTGGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAACGGGTCGCGATCG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGCAATATG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGTTCGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGCATGTCGAT-1_FCA7167219        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AAACGGGCATTGGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAACGGGTCGCGATCG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGCAATATG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGTTCGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGCATGTCGAT-1_FCA7167219                     decidua_immune   13_PCW   
...                                                          ...      ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AAACGGGCATTGGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAACGGGTCGCGATCG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGCAATATG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGTTCGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGCATGTCGAT-1_FCA7167219           6          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AAACGGGCATTGGCGC-1_FCA7167219                                        1      0   
AAACGGGTCGCGATCG-1_FCA7167219                                        1      0   
AAAGATGAGCAATATG-1_FCA7167219                                        1      0   
AAAGATGAGTTCGCGC-1_FCA7167219                                        1      0   
AAAGATGCATG

In [51]:
# subsetting the adata object to final cells
adata = adata[list(nodoublet_cell_IDs.index), :].copy()
adata

AnnData object with n_obs × n_vars = 378558 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feature_types-1

In [52]:
# adding metadata
for col in nodoublet_cell_IDs.columns:
    print(col)
    adata.obs[col] = nodoublet_cell_IDs.loc[adata.obs_names,col]

n_genes
sample
technology
tissue
dev_age
donor
dataset
run
number_of_individuals_multiplexed
batch
percent_mito
n_counts
scrublet_score
scrublet_cluster_score
bh_pval
is_doublet
celltype_predictions
probabilities
barcode_sample_copy
souporcell_assignment
inter_ind_doublet
S_score
G2M_score
phase
origin_M_F
is_doublet_0.05
is_doublet_0.01


In [53]:
# excluding soupy genes as per notebook M3a-1

# gene stats for cells
gene_stats_sc = pd.read_csv(save_path + 'gene_filter_cells_upd_20211111.csv', index_col=0)

# gene stats for nuclei
gene_stats_sn = pd.read_csv(save_path + 'gene_filter_nuclei_upd_20211111.csv', index_col=0)

genes2keep_sc = list(gene_stats_sc[gene_stats_sc['Selected'] == True].index)
genes2keep_sn = list(gene_stats_sn[gene_stats_sn['Selected'] == True].index)

# overlap
genes2keep = list(set(genes2keep_sc) & set(genes2keep_sn))

print(len(genes2keep))

adata = adata[:,list(set(genes2keep) & set(adata.var_names))].copy()
adata

# cell cycle related - no need to, seems like all of those have been removed by soupy gene filter
#cleaned_up_genes_cc = pd.read_csv(save_path + '', index_col=0)

7849


AnnData object with n_obs × n_vars = 378558 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature

In [54]:
# discarding contaminants labelled in notebook S1-1
annot = pd.read_csv(save_path + 'obs_table_inv_troph_v1_contaminants.csv',
                          index_col=0)
annot

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (29) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AGGGTGAGTAAAGGAG-1_FCA7167219           5291        FCA7167219   
CTGATAGAGCCCAGCT-1_FCA7167219           4070        FCA7167219   
GCGCGATAGATATGGT-1_FCA7167219            506        FCA7167219   
AGGGTGAGTAAAGGAG-1_FCA7167221            819        FCA7167221   
ATTACTCTCTGCGGCA-1_FCA7167221            655        FCA7167221   
...                                      ...               ...   
TTTCACCCAAGTGTTT-1_Pla_Camb10714920     4770  Pla_Camb10714920   
TTTCTTGCATCTTGAG-1_Pla_Camb10714920      886  Pla_Camb10714920   
TTTGTCTAGACAACAG-1_Pla_Camb10714920     3979  Pla_Camb10714920   
TTTGTCTAGGCTGGCT-1_Pla_Camb10714920     3445  Pla_Camb10714920   
TTTGTGGCACAGAAAC-1_Pla_Camb10714920     6044  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AGGGTGAGTAAAGGAG-1_FCA7167219        10X_3'_scRNA-seq   
CTGATAGAGCCCAGCT-1_FCA7167219        10X_3'_scRNA-seq   
GCGCGATAGATATGGT-1_FCA7167219        10X_3'_scRNA-seq   
AGGGTGAGTAAAGGAG-1_FCA7167221        10X_3'_scRNA-seq   
ATTACTCTCTGCGGCA-1_FCA7167221        10X_3'_scRNA-seq   
...                                               ...   
TTTCACCCAAGTGTTT-1_Pla_Camb10714920      10X_multiome   
TTTCTTGCATCTTGAG-1_Pla_Camb10714920      10X_multiome   
TTTGTCTAGACAACAG-1_Pla_Camb10714920      10X_multiome   
TTTGTCTAGGCTGGCT-1_Pla_Camb10714920      10X_multiome   
TTTGTGGCACAGAAAC-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AGGGTGAGTAAAGGAG-1_FCA7167219                     decidua_immune   13_PCW   
CTGATAGAGCCCAGCT-1_FCA7167219                     decidua_immune   13_PCW   
GCGCGATAGATATGGT-1_FCA7167219                     decidua_immune   13_PCW   
AGGGTGAGTAAAGGAG-1_FCA7167221                     decidua_immune   11_PCW   
ATTACTCTCTGCGGCA-1_FCA7167221                     decidua_immune   11_PCW   
...                                                          ...      ...   
TTTCACCCAAGTGTTT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTCTTGCATCTTGAG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTCTAGACAACAG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTCTAGGCTGGCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGGCACAGAAAC-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AGGGTGAGTAAAGGAG-1_FCA7167219           6          Vento_Nature  NaN   
CTGATAGAGCCCAGCT-1_FCA7167219           6          Vento_Nature  NaN   
GCGCGATAGATATGGT-1_FCA7167219           6          Vento_Nature  NaN   
AGGGTGAGTAAAGGAG-1_FCA7167221           7          Vento_Nature  NaN   
ATTACTCTCTGCGGCA-1_FCA7167221           7          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTCACCCAAGTGTTT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTCTTGCATCTTGAG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTCTAGACAACAG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTCTAGGCTGGCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGGCACAGAAAC-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AGGGTGAGTAAAGGAG-1_FCA7167219                                        1      0   
CTGATAGAGCCCAGCT-1_FCA7167219                                        1      0   
GCGCGATAGATATGGT-1_FCA7167219                                        1      0   
AGGGTGAGTAAAGGAG-1_FCA7167221                                        1      1   
ATTACTCTCTG

In [55]:
# subset to only troph
adata = adata[annot.index,:].copy()
adata.obs['inv_troph_contaminants_v1'] = annot.loc[list(adata.obs_names),'inv_troph_contaminants_v1']
adata.obs['inv_troph_contaminants_v1'].value_counts()


keeping         16079
contaminants      382
Name: inv_troph_contaminants_v1, dtype: int64

In [58]:
# remove contaminants after cleanup 1 in S1-1 notebook
adata = adata[adata.obs['inv_troph_contaminants_v1'] == 'keeping'].copy()

In [59]:
adata

AnnData object with n_obs × n_vars = 16079 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'inv_troph_contaminants_v1'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-

In [60]:
# no CC-assoc gene filtering here

# optimal n_PCs = 5 here

In [61]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [62]:
adata

AnnData object with n_obs × n_vars = 16079 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'inv_troph_contaminants_v1'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-

In [63]:
# here we subset to HVGs, not accounting for sample batch here - it breaks the HVG finding (not enough batch representation?)
sc.pp.highly_variable_genes(adata, min_mean=0.0125, max_mean=3, min_disp=0.5,
                           subset=True)

In [64]:
adata

AnnData object with n_obs × n_vars = 16079 × 1764
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'inv_troph_contaminants_v1'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-

#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [65]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 16079 cells, 1764 vars, 1 batches,
         1 labels, and 0 proteins. Also registered 1 extra categorical covariates and 0 extra
         continuous covariates.                                                              
INFO     Please do not further modify adata until model is trained.                          


### 14.11.2021 Running scVI after:

- removing soupy genes as per LF approach (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell)

In [68]:
models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

n_latent_values = [5,10]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 5
n_latent_value 10


In [69]:
latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_Trophoblast_compartment_only_inv_troph_v2_with_LF_gene_filter_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 10
Epoch 400/400: 100%|██████████████████████████████████████████████████████████████████| 400/400 [07:22<00:00,  1.11s/it, loss=736, v_num=1]


# Running on only invading trophoblast, v3


Subsetted by unbiased clusteing of the manifold with all cell states as calculated above

In [70]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [71]:
# reading IDs of final cells to keep (after also excluding doublets by GEX, done in notebook M3)
nodoublet_cell_IDs = pd.read_csv(save_path + 'selected_droplets_no_doublets_in_M1_prelim_analysis.csv', index_col=0)
nodoublet_cell_IDs

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AAACGGGCATTGGCGC-1_FCA7167219           1941        FCA7167219   
AAACGGGTCGCGATCG-1_FCA7167219           1246        FCA7167219   
AAAGATGAGCAATATG-1_FCA7167219           1516        FCA7167219   
AAAGATGAGTTCGCGC-1_FCA7167219           2099        FCA7167219   
AAAGATGCATGTCGAT-1_FCA7167219           1636        FCA7167219   
...                                      ...               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920     2409  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920     3116  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AAACGGGCATTGGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAACGGGTCGCGATCG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGCAATATG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGTTCGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGCATGTCGAT-1_FCA7167219        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AAACGGGCATTGGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAACGGGTCGCGATCG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGCAATATG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGTTCGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGCATGTCGAT-1_FCA7167219                     decidua_immune   13_PCW   
...                                                          ...      ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AAACGGGCATTGGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAACGGGTCGCGATCG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGCAATATG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGTTCGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGCATGTCGAT-1_FCA7167219           6          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AAACGGGCATTGGCGC-1_FCA7167219                                        1      0   
AAACGGGTCGCGATCG-1_FCA7167219                                        1      0   
AAAGATGAGCAATATG-1_FCA7167219                                        1      0   
AAAGATGAGTTCGCGC-1_FCA7167219                                        1      0   
AAAGATGCATG

In [72]:
# subsetting the adata object to final cells
adata = adata[list(nodoublet_cell_IDs.index), :].copy()
adata

AnnData object with n_obs × n_vars = 378558 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feature_types-1

In [73]:
# adding metadata
for col in nodoublet_cell_IDs.columns:
    print(col)
    adata.obs[col] = nodoublet_cell_IDs.loc[adata.obs_names,col]

n_genes
sample
technology
tissue
dev_age
donor
dataset
run
number_of_individuals_multiplexed
batch
percent_mito
n_counts
scrublet_score
scrublet_cluster_score
bh_pval
is_doublet
celltype_predictions
probabilities
barcode_sample_copy
souporcell_assignment
inter_ind_doublet
S_score
G2M_score
phase
origin_M_F
is_doublet_0.05
is_doublet_0.01


In [74]:
# excluding soupy genes as per notebook M3a-1

# gene stats for cells
gene_stats_sc = pd.read_csv(save_path + 'gene_filter_cells_upd_20211111.csv', index_col=0)

# gene stats for nuclei
gene_stats_sn = pd.read_csv(save_path + 'gene_filter_nuclei_upd_20211111.csv', index_col=0)

genes2keep_sc = list(gene_stats_sc[gene_stats_sc['Selected'] == True].index)
genes2keep_sn = list(gene_stats_sn[gene_stats_sn['Selected'] == True].index)

# overlap
genes2keep = list(set(genes2keep_sc) & set(genes2keep_sn))

print(len(genes2keep))

adata = adata[:,list(set(genes2keep) & set(adata.var_names))].copy()
adata

# cell cycle related - no need to, seems like all of those have been removed by soupy gene filter
#cleaned_up_genes_cc = pd.read_csv(save_path + '', index_col=0)

7849


AnnData object with n_obs × n_vars = 378558 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature

In [75]:
# discarding contaminants labelled in notebook S1-2
annot = pd.read_csv(save_path + 'obs_table_inv_troph_v2_contaminants.csv',
                          index_col=0)
annot

n_genes            sample  \
barcode_sample                                                   
AGGGTGAGTAAAGGAG-1_FCA7167219           5291        FCA7167219   
CTGATAGAGCCCAGCT-1_FCA7167219           4070        FCA7167219   
GCGCGATAGATATGGT-1_FCA7167219            506        FCA7167219   
ATTACTCTCTGCGGCA-1_FCA7167221            655        FCA7167221   
CTGATAGAGCCCAGCT-1_FCA7167221            412        FCA7167221   
...                                      ...               ...   
TTTAGCAAGCGGCTGT-1_Pla_Camb10714920     4153  Pla_Camb10714920   
TTTCTTGCATCTTGAG-1_Pla_Camb10714920      886  Pla_Camb10714920   
TTTGTCTAGACAACAG-1_Pla_Camb10714920     3979  Pla_Camb10714920   
TTTGTCTAGGCTGGCT-1_Pla_Camb10714920     3445  Pla_Camb10714920   
TTTGTGGCACAGAAAC-1_Pla_Camb10714920     6044  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AGGGTGAGTAAAGGAG-1_FCA7167219        10X_3'_scRNA-seq   
CTGATAGAGCCCAGCT-1_FCA7167219        10X_3'_scRNA-seq   
GCGCGATAGATATGGT-1_FCA7167219        10X_3'_scRNA-seq   
ATTACTCTCTGCGGCA-1_FCA7167221        10X_3'_scRNA-seq   
CTGATAGAGCCCAGCT-1_FCA7167221        10X_3'_scRNA-seq   
...                                               ...   
TTTAGCAAGCGGCTGT-1_Pla_Camb10714920      10X_multiome   
TTTCTTGCATCTTGAG-1_Pla_Camb10714920      10X_multiome   
TTTGTCTAGACAACAG-1_Pla_Camb10714920      10X_multiome   
TTTGTCTAGGCTGGCT-1_Pla_Camb10714920      10X_multiome   
TTTGTGGCACAGAAAC-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AGGGTGAGTAAAGGAG-1_FCA7167219                     decidua_immune   13_PCW   
CTGATAGAGCCCAGCT-1_FCA7167219                     decidua_immune   13_PCW   
GCGCGATAGATATGGT-1_FCA7167219                     decidua_immune   13_PCW   
ATTACTCTCTGCGGCA-1_FCA7167221                     decidua_immune   11_PCW   
CTGATAGAGCCCAGCT-1_FCA7167221                     decidua_immune   11_PCW   
...                                                          ...      ...   
TTTAGCAAGCGGCTGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTCTTGCATCTTGAG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTCTAGACAACAG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTCTAGGCTGGCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGGCACAGAAAC-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AGGGTGAGTAAAGGAG-1_FCA7167219           6          Vento_Nature  NaN   
CTGATAGAGCCCAGCT-1_FCA7167219           6          Vento_Nature  NaN   
GCGCGATAGATATGGT-1_FCA7167219           6          Vento_Nature  NaN   
ATTACTCTCTGCGGCA-1_FCA7167221           7          Vento_Nature  NaN   
CTGATAGAGCCCAGCT-1_FCA7167221           7          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTAGCAAGCGGCTGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTCTTGCATCTTGAG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTCTAGACAACAG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTCTAGGCTGGCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGGCACAGAAAC-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AGGGTGAGTAAAGGAG-1_FCA7167219                                        1      0   
CTGATAGAGCCCAGCT-1_FCA7167219                                        1      0   
GCGCGATAGATATGGT-1_FCA7167219                                        1      0   
ATTACTCTCTGCGGCA-1_FCA7167221                                        1      1   
CTGATAGAGCC

In [76]:
# subset to only troph
adata = adata[annot.index,:].copy()
adata.obs['inv_troph_contaminants_v2'] = annot.loc[list(adata.obs_names),'inv_troph_contaminants_v2']
adata.obs['inv_troph_contaminants_v2'].value_counts()


keeping         15323
contaminants      756
Name: inv_troph_contaminants_v2, dtype: int64

In [77]:
# remove contaminants after cleanup 1 in S1-2 notebook
adata = adata[adata.obs['inv_troph_contaminants_v2'] == 'keeping'].copy()

In [78]:
adata

AnnData object with n_obs × n_vars = 15323 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'inv_troph_contaminants_v2'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-

In [80]:
# no CC-assoc gene filtering here

# optimal n_PCs = 4 and 11 here

In [81]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [82]:
adata

AnnData object with n_obs × n_vars = 15323 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'inv_troph_contaminants_v2'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-

In [83]:
# here we subset to HVGs, not accounting for sample batch here - it breaks the HVG finding (not enough batch representation?)
sc.pp.highly_variable_genes(adata, min_mean=0.0125, max_mean=3, min_disp=0.5,
                           subset=True)

In [84]:
adata

AnnData object with n_obs × n_vars = 15323 × 1752
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'inv_troph_contaminants_v2'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-

#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [85]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 15323 cells, 1752 vars, 1 batches,
         1 labels, and 0 proteins. Also registered 1 extra categorical covariates and 0 extra
         continuous covariates.                                                              
INFO     Please do not further modify adata until model is trained.                          


### 14.11.2021 Running scVI after:

- removing soupy genes as per LF approach (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell)

In [86]:
models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

n_latent_values = [4,11]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 4
n_latent_value 11


In [87]:
latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_Trophoblast_compartment_only_inv_troph_v3_with_LF_gene_filter_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 4
Epoch 400/400: 100%|██████████████████████████████████████████████████████████████████| 400/400 [06:57<00:00,  1.04s/it, loss=695, v_num=1]


GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 11
Epoch 400/400: 100%|██████████████████████████████████████████████████████████████████| 400/400 [06:59<00:00,  1.05s/it, loss=708, v_num=1]


# Running on all trophoblast, final manifold calculation


Subsetted by unbiased clusteing of the manifold with all cell states as calculated above

In [88]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [89]:
# reading IDs of final cells to keep (after also excluding doublets by GEX, done in notebook M3)
nodoublet_cell_IDs = pd.read_csv(save_path + 'selected_droplets_no_doublets_in_M1_prelim_analysis.csv', index_col=0)
nodoublet_cell_IDs

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AAACGGGCATTGGCGC-1_FCA7167219           1941        FCA7167219   
AAACGGGTCGCGATCG-1_FCA7167219           1246        FCA7167219   
AAAGATGAGCAATATG-1_FCA7167219           1516        FCA7167219   
AAAGATGAGTTCGCGC-1_FCA7167219           2099        FCA7167219   
AAAGATGCATGTCGAT-1_FCA7167219           1636        FCA7167219   
...                                      ...               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920     2409  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920     3116  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AAACGGGCATTGGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAACGGGTCGCGATCG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGCAATATG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGTTCGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGCATGTCGAT-1_FCA7167219        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AAACGGGCATTGGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAACGGGTCGCGATCG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGCAATATG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGTTCGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGCATGTCGAT-1_FCA7167219                     decidua_immune   13_PCW   
...                                                          ...      ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AAACGGGCATTGGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAACGGGTCGCGATCG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGCAATATG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGTTCGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGCATGTCGAT-1_FCA7167219           6          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AAACGGGCATTGGCGC-1_FCA7167219                                        1      0   
AAACGGGTCGCGATCG-1_FCA7167219                                        1      0   
AAAGATGAGCAATATG-1_FCA7167219                                        1      0   
AAAGATGAGTTCGCGC-1_FCA7167219                                        1      0   
AAAGATGCATG

In [90]:
# subsetting the adata object to final cells
adata = adata[list(nodoublet_cell_IDs.index), :].copy()
adata

AnnData object with n_obs × n_vars = 378558 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feature_types-1

In [91]:
# adding metadata
for col in nodoublet_cell_IDs.columns:
    print(col)
    adata.obs[col] = nodoublet_cell_IDs.loc[adata.obs_names,col]

n_genes
sample
technology
tissue
dev_age
donor
dataset
run
number_of_individuals_multiplexed
batch
percent_mito
n_counts
scrublet_score
scrublet_cluster_score
bh_pval
is_doublet
celltype_predictions
probabilities
barcode_sample_copy
souporcell_assignment
inter_ind_doublet
S_score
G2M_score
phase
origin_M_F
is_doublet_0.05
is_doublet_0.01


In [92]:
# excluding soupy genes as per notebook M3a-1

# gene stats for cells
gene_stats_sc = pd.read_csv(save_path + 'gene_filter_cells_upd_20211111.csv', index_col=0)

# gene stats for nuclei
gene_stats_sn = pd.read_csv(save_path + 'gene_filter_nuclei_upd_20211111.csv', index_col=0)

genes2keep_sc = list(gene_stats_sc[gene_stats_sc['Selected'] == True].index)
genes2keep_sn = list(gene_stats_sn[gene_stats_sn['Selected'] == True].index)

# overlap
genes2keep = list(set(genes2keep_sc) & set(genes2keep_sn))

print(len(genes2keep))

adata = adata[:,list(set(genes2keep) & set(adata.var_names))].copy()
adata

# cell cycle related - no need to, seems like all of those have been removed by soupy gene filter
#cleaned_up_genes_cc = pd.read_csv(save_path + '', index_col=0)

7849


AnnData object with n_obs × n_vars = 378558 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature

In [93]:
# discarding contaminants labelled in notebook S1-2
annot = pd.read_csv(save_path + 'obs_selected_final_troph.csv',
                          index_col=0)
annot

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AGGGTGAGTAAAGGAG-1_FCA7167219           5291        FCA7167219   
CTGATAGAGCCCAGCT-1_FCA7167219           4070        FCA7167219   
GCGCGATAGATATGGT-1_FCA7167219            506        FCA7167219   
ATTACTCTCTGCGGCA-1_FCA7167221            655        FCA7167221   
CTGATAGAGCCCAGCT-1_FCA7167221            412        FCA7167221   
...                                      ...               ...   
TTTGTGGCATGGCCTG-1_Pla_Camb10714920     4195  Pla_Camb10714920   
TTTGTGTTCGCTCACT-1_Pla_Camb10714920     1629  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AGGGTGAGTAAAGGAG-1_FCA7167219        10X_3'_scRNA-seq   
CTGATAGAGCCCAGCT-1_FCA7167219        10X_3'_scRNA-seq   
GCGCGATAGATATGGT-1_FCA7167219        10X_3'_scRNA-seq   
ATTACTCTCTGCGGCA-1_FCA7167221        10X_3'_scRNA-seq   
CTGATAGAGCCCAGCT-1_FCA7167221        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGGCATGGCCTG-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCGCTCACT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AGGGTGAGTAAAGGAG-1_FCA7167219                     decidua_immune   13_PCW   
CTGATAGAGCCCAGCT-1_FCA7167219                     decidua_immune   13_PCW   
GCGCGATAGATATGGT-1_FCA7167219                     decidua_immune   13_PCW   
ATTACTCTCTGCGGCA-1_FCA7167221                     decidua_immune   11_PCW   
CTGATAGAGCCCAGCT-1_FCA7167221                     decidua_immune   11_PCW   
...                                                          ...      ...   
TTTGTGGCATGGCCTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCGCTCACT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AGGGTGAGTAAAGGAG-1_FCA7167219           6          Vento_Nature  NaN   
CTGATAGAGCCCAGCT-1_FCA7167219           6          Vento_Nature  NaN   
GCGCGATAGATATGGT-1_FCA7167219           6          Vento_Nature  NaN   
ATTACTCTCTGCGGCA-1_FCA7167221           7          Vento_Nature  NaN   
CTGATAGAGCCCAGCT-1_FCA7167221           7          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGGCATGGCCTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCGCTCACT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AGGGTGAGTAAAGGAG-1_FCA7167219                                        1      0   
CTGATAGAGCCCAGCT-1_FCA7167219                                        1      0   
GCGCGATAGATATGGT-1_FCA7167219                                        1      0   
ATTACTCTCTGCGGCA-1_FCA7167221                                        1      1   
CTGATAGAGCC

In [94]:
# subset to only final troph
adata = adata[annot.index,:].copy()

In [95]:
adata

AnnData object with n_obs × n_vars = 75855 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_

In [96]:
# no CC-assoc gene filtering here

# optimal n_PCs = 5 and 11 here

In [97]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [98]:
adata

AnnData object with n_obs × n_vars = 75855 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_

In [99]:
# here we subset to HVGs, not accounting for sample batch here - it breaks the HVG finding (not enough batch representation?)
sc.pp.highly_variable_genes(adata, min_mean=0.0125, max_mean=3, min_disp=0.5,
                           subset=True)

In [100]:
adata

AnnData object with n_obs × n_vars = 75855 × 1885
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_

#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [101]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 75855 cells, 1885 vars, 1 batches,
         1 labels, and 0 proteins. Also registered 1 extra categorical covariates and 0 extra
         continuous covariates.                                                              
INFO     Please do not further modify adata until model is trained.                          


### 14.11.2021 Running scVI after:

- removing soupy genes as per LF approach (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell)

In [102]:
models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

# just a few values here, it was 17 PCs I used in the conventional analysis
n_latent_values = [5]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 5


In [103]:
latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_Trophoblast_compartment_v3_final_with_LF_gene_filter_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 5
Epoch 105/105: 100%|██████████████████████████████████████████████████████████████████| 105/105 [09:08<00:00,  5.22s/it, loss=740, v_num=1]


# Running on only structural/supporting compartment (dS + uSMC) 


Subsetted by unbiased clusteing of the manifold with all cell states as calculated

In [5]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [6]:
# reading IDs of final cells to keep (after also excluding doublets by GEX, done in notebook M3)
nodoublet_cell_IDs = pd.read_csv(save_path + 'selected_droplets_no_doublets_in_M1_prelim_analysis.csv', index_col=0)
nodoublet_cell_IDs

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AAACGGGCATTGGCGC-1_FCA7167219           1941        FCA7167219   
AAACGGGTCGCGATCG-1_FCA7167219           1246        FCA7167219   
AAAGATGAGCAATATG-1_FCA7167219           1516        FCA7167219   
AAAGATGAGTTCGCGC-1_FCA7167219           2099        FCA7167219   
AAAGATGCATGTCGAT-1_FCA7167219           1636        FCA7167219   
...                                      ...               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920     2409  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920     3116  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AAACGGGCATTGGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAACGGGTCGCGATCG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGCAATATG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGTTCGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGCATGTCGAT-1_FCA7167219        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AAACGGGCATTGGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAACGGGTCGCGATCG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGCAATATG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGTTCGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGCATGTCGAT-1_FCA7167219                     decidua_immune   13_PCW   
...                                                          ...      ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AAACGGGCATTGGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAACGGGTCGCGATCG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGCAATATG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGTTCGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGCATGTCGAT-1_FCA7167219           6          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AAACGGGCATTGGCGC-1_FCA7167219                                        1      0   
AAACGGGTCGCGATCG-1_FCA7167219                                        1      0   
AAAGATGAGCAATATG-1_FCA7167219                                        1      0   
AAAGATGAGTTCGCGC-1_FCA7167219                                        1      0   
AAAGATGCATG

In [7]:
# subsetting the adata object to final cells
adata = adata[list(nodoublet_cell_IDs.index), :].copy()
adata

AnnData object with n_obs × n_vars = 378558 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feature_types-1

In [8]:
# adding metadata
for col in nodoublet_cell_IDs.columns:
    print(col)
    adata.obs[col] = nodoublet_cell_IDs.loc[adata.obs_names,col]

n_genes
sample
technology
tissue
dev_age
donor
dataset
run
number_of_individuals_multiplexed
batch
percent_mito
n_counts
scrublet_score
scrublet_cluster_score
bh_pval
is_doublet
celltype_predictions
probabilities
barcode_sample_copy
souporcell_assignment
inter_ind_doublet
S_score
G2M_score
phase
origin_M_F
is_doublet_0.05
is_doublet_0.01


In [9]:
# excluding soupy genes as per notebook M3a-1

# gene stats for cells
gene_stats_sc = pd.read_csv(save_path + 'gene_filter_cells_upd_20211111.csv', index_col=0)

# gene stats for nuclei
gene_stats_sn = pd.read_csv(save_path + 'gene_filter_nuclei_upd_20211111.csv', index_col=0)

genes2keep_sc = list(gene_stats_sc[gene_stats_sc['Selected'] == True].index)
genes2keep_sn = list(gene_stats_sn[gene_stats_sn['Selected'] == True].index)

# overlap
genes2keep = list(set(genes2keep_sc) & set(genes2keep_sn))

print(len(genes2keep))

adata = adata[:,list(set(genes2keep) & set(adata.var_names))].copy()
adata

# cell cycle related - no need to, seems like all of those have been removed by soupy gene filter
#cleaned_up_genes_cc = pd.read_csv(save_path + '', index_col=0)

7849


AnnData object with n_obs × n_vars = 378558 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature

In [10]:
# subsetting to only trophoblast according to coarse annotation done in notebook M4
annot_coarse = pd.read_csv(save_path + 'obs_table_with_coarse_annot_from_M4_notebook_all_cell_states.csv',
                          index_col=0)
adata.obs['annot_coarse'] = annot_coarse.loc[adata.obs_names,'annot_coarse']
adata.obs['annot_coarse'].value_counts()

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6,28) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


dS_uSMC        158106
Trophoblast     81704
Myeloid         43997
NK              30132
T               19244
Epithelial      18222
Endothelial     12689
fF              12633
PV               1831
Name: annot_coarse, dtype: int64

In [11]:
adata = adata[adata.obs['annot_coarse'] == 'dS_uSMC'].copy()

In [12]:
adata

AnnData object with n_obs × n_vars = 158106 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_i

In [13]:
# no CC-assoc gene filtering here

# optimal n_PCs = 8 here

In [14]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [15]:
adata

AnnData object with n_obs × n_vars = 158106 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_i

In [16]:
# here we subset to HVGs, not accounting for sample batch here - it breaks the HVG finding (not enough batch representation?)
sc.pp.highly_variable_genes(adata, min_mean=0.0125, max_mean=3, min_disp=0.5,
                           subset=True)

In [17]:
adata

AnnData object with n_obs × n_vars = 158106 × 1998
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_i

#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [18]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 158106 cells, 1998 vars, 1        
         batches, 1 labels, and 0 proteins. Also registered 1 extra categorical covariates   
         and 0 extra continuous covariates.                                                  
INFO     Please do not further modify adata until model is trained.                          


### 14.11.2021 Running scVI after:

- removing soupy genes as per LF approach (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell)

In [19]:
models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

n_latent_values = [8]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 8


In [20]:
latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_dS_uSMC_compartment_v1_with_LF_gene_filter_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 8
Epoch 51/51: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 51/51 [11:47<00:00, 13.87s/it, loss=531, v_num=1]


# Running on only NK + ILC compartment


Subsetted by unbiased clusteing of the manifold with all cell states as calculated above

In [62]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [63]:
# reading IDs of final cells to keep (after also excluding doublets by GEX, done in notebook M3)
nodoublet_cell_IDs = pd.read_csv(save_path + 'selected_droplets_no_doublets_in_M1_prelim_analysis.csv', index_col=0)
nodoublet_cell_IDs

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AAACGGGCATTGGCGC-1_FCA7167219           1941        FCA7167219   
AAACGGGTCGCGATCG-1_FCA7167219           1246        FCA7167219   
AAAGATGAGCAATATG-1_FCA7167219           1516        FCA7167219   
AAAGATGAGTTCGCGC-1_FCA7167219           2099        FCA7167219   
AAAGATGCATGTCGAT-1_FCA7167219           1636        FCA7167219   
...                                      ...               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920     2409  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920     3116  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AAACGGGCATTGGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAACGGGTCGCGATCG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGCAATATG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGTTCGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGCATGTCGAT-1_FCA7167219        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AAACGGGCATTGGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAACGGGTCGCGATCG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGCAATATG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGTTCGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGCATGTCGAT-1_FCA7167219                     decidua_immune   13_PCW   
...                                                          ...      ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AAACGGGCATTGGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAACGGGTCGCGATCG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGCAATATG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGTTCGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGCATGTCGAT-1_FCA7167219           6          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AAACGGGCATTGGCGC-1_FCA7167219                                        1      0   
AAACGGGTCGCGATCG-1_FCA7167219                                        1      0   
AAAGATGAGCAATATG-1_FCA7167219                                        1      0   
AAAGATGAGTTCGCGC-1_FCA7167219                                        1      0   
AAAGATGCATG

In [64]:
# subsetting the adata object to final cells
adata = adata[list(nodoublet_cell_IDs.index), :].copy()
adata

AnnData object with n_obs × n_vars = 378558 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feature_types-1

In [65]:
# adding metadata
for col in nodoublet_cell_IDs.columns:
    print(col)
    adata.obs[col] = nodoublet_cell_IDs.loc[adata.obs_names,col]

n_genes
sample
technology
tissue
dev_age
donor
dataset
run
number_of_individuals_multiplexed
batch
percent_mito
n_counts
scrublet_score
scrublet_cluster_score
bh_pval
is_doublet
celltype_predictions
probabilities
barcode_sample_copy
souporcell_assignment
inter_ind_doublet
S_score
G2M_score
phase
origin_M_F
is_doublet_0.05
is_doublet_0.01


In [66]:
# subsetting to only trophoblast according to coarse annotation done in notebook M4
annot_coarse = pd.read_csv(save_path + 'obs_table_with_coarse_annot_from_M4_notebook_all_cell_states.csv',
                          index_col=0)
adata.obs['annot_coarse'] = annot_coarse.loc[adata.obs_names,'annot_coarse']
adata.obs['annot_coarse'].value_counts()

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6,28) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


dS_uSMC        158106
Trophoblast     81704
Myeloid         43997
NK              30132
T               19244
Epithelial      18222
Endothelial     12689
fF              12633
PV               1831
Name: annot_coarse, dtype: int64

In [67]:
adata = adata[adata.obs['annot_coarse'] == 'NK'].copy()

In [68]:
adata

AnnData object with n_obs × n_vars = 30132 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_i

In [69]:
# CC-assoc gene filtering here

cleaned_up_genes = pd.read_csv(save_path + 'cleaned_up_genes_in_S3_notebook_NK_20211114.csv', index_col=0)

adata = adata[:,cleaned_up_genes.index].copy()
adata

# optimal n_PCs = 10 here

AnnData object with n_obs × n_vars = 30132 × 30607
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_i

In [70]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [71]:
adata

AnnData object with n_obs × n_vars = 30132 × 30607
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_i

In [72]:
# here we subset to HVGs, not accounting for sample batch here - it breaks the HVG finding (not enough batch representation?)
sc.pp.highly_variable_genes(adata, min_mean=0.0125, max_mean=3, min_disp=0.5,
                           subset=True)

In [73]:
adata

AnnData object with n_obs × n_vars = 30132 × 3815
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_id

#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [74]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 30132 cells, 3815 vars, 1 batches,
         1 labels, and 0 proteins. Also registered 1 extra categorical covariates and 0 extra
         continuous covariates.                                                              
INFO     Please do not further modify adata until model is trained.                          


### 14.11.2021 Running scVI after:

- removing soupy genes as per LF approach (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell)

In [75]:
# this one is without soupy gene removal

models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

n_latent_values = [8]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 8


In [76]:
# without soupy gene filtering and with CC-assoc gene filtering

latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_NK_compartment_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 8
Epoch 265/265: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 265/265 [11:57<00:00,  2.71s/it, loss=719, v_num=1]


In [ ]:
# below is with soupy gene filter and without CC-assoc gene filtering

In [35]:
models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

# just a few values here, it was 17 PCs I used in the conventional analysis
n_latent_values = [8]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 8


In [36]:
latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_NK_compartment_with_LF_gene_filter_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 8
Epoch 265/265: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 265/265 [11:29<00:00,  2.60s/it, loss=254, v_num=1]


# Running on only T compartment


Subsetted by unbiased clusteing of the manifold with all cell states as calculated above with n_latent=

In [77]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [78]:
# reading IDs of final cells to keep (after also excluding doublets by GEX, done in notebook M3)
nodoublet_cell_IDs = pd.read_csv(save_path + 'selected_droplets_no_doublets_in_M1_prelim_analysis.csv', index_col=0)
nodoublet_cell_IDs

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AAACGGGCATTGGCGC-1_FCA7167219           1941        FCA7167219   
AAACGGGTCGCGATCG-1_FCA7167219           1246        FCA7167219   
AAAGATGAGCAATATG-1_FCA7167219           1516        FCA7167219   
AAAGATGAGTTCGCGC-1_FCA7167219           2099        FCA7167219   
AAAGATGCATGTCGAT-1_FCA7167219           1636        FCA7167219   
...                                      ...               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920     2409  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920     3116  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AAACGGGCATTGGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAACGGGTCGCGATCG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGCAATATG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGTTCGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGCATGTCGAT-1_FCA7167219        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AAACGGGCATTGGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAACGGGTCGCGATCG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGCAATATG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGTTCGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGCATGTCGAT-1_FCA7167219                     decidua_immune   13_PCW   
...                                                          ...      ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AAACGGGCATTGGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAACGGGTCGCGATCG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGCAATATG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGTTCGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGCATGTCGAT-1_FCA7167219           6          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AAACGGGCATTGGCGC-1_FCA7167219                                        1      0   
AAACGGGTCGCGATCG-1_FCA7167219                                        1      0   
AAAGATGAGCAATATG-1_FCA7167219                                        1      0   
AAAGATGAGTTCGCGC-1_FCA7167219                                        1      0   
AAAGATGCATG

In [79]:
# subsetting the adata object to final cells
adata = adata[list(nodoublet_cell_IDs.index), :].copy()
adata

AnnData object with n_obs × n_vars = 378558 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feature_types-1

In [80]:
# adding metadata
for col in nodoublet_cell_IDs.columns:
    print(col)
    adata.obs[col] = nodoublet_cell_IDs.loc[adata.obs_names,col]

n_genes
sample
technology
tissue
dev_age
donor
dataset
run
number_of_individuals_multiplexed
batch
percent_mito
n_counts
scrublet_score
scrublet_cluster_score
bh_pval
is_doublet
celltype_predictions
probabilities
barcode_sample_copy
souporcell_assignment
inter_ind_doublet
S_score
G2M_score
phase
origin_M_F
is_doublet_0.05
is_doublet_0.01


In [81]:
# excluding soupy genes as per notebook M2

# gene stats for cells
gene_stats_sc = pd.read_csv(save_path + 'gene_filter_cells_upd_20211111.csv', index_col=0)

# gene stats for nuclei
gene_stats_sn = pd.read_csv(save_path + 'gene_filter_nuclei_upd_20211111.csv', index_col=0)

genes2keep_sc = list(gene_stats_sc[gene_stats_sc['Selected'] == True].index)
genes2keep_sn = list(gene_stats_sn[gene_stats_sn['Selected'] == True].index)

# overlap
genes2keep = list(set(genes2keep_sc) & set(genes2keep_sn))

print(len(genes2keep))

adata = adata[:,list(set(genes2keep) & set(adata.var_names))].copy()
adata

# cell cycle related - no need to, seems like all of those have been removed by soupy gene filter
#cleaned_up_genes_cc = pd.read_csv(save_path + '', index_col=0)

7849


AnnData object with n_obs × n_vars = 378558 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature

In [82]:
# subsetting to only trophoblast according to coarse annotation done in notebook M4
annot_coarse = pd.read_csv(save_path + 'obs_table_with_coarse_annot_from_M4_notebook_all_cell_states.csv',
                          index_col=0)
adata.obs['annot_coarse'] = annot_coarse.loc[adata.obs_names,'annot_coarse']
adata.obs['annot_coarse'].value_counts()

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6,28) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


dS_uSMC        158106
Trophoblast     81704
Myeloid         43997
NK              30132
T               19244
Epithelial      18222
Endothelial     12689
fF              12633
PV               1831
Name: annot_coarse, dtype: int64

In [83]:
adata = adata[adata.obs['annot_coarse'] == 'T'].copy()

In [84]:
adata

AnnData object with n_obs × n_vars = 19244 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_id

In [85]:
# CC-assoc gene filtering here

cleaned_up_genes = pd.read_csv(save_path + 'cleaned_up_genes_in_S4_notebook_T_20211114.csv', index_col=0)

adata = adata[:,cleaned_up_genes.index].copy()
adata

# optimal n_PCs = 9 here

KeyError: "Values ['A1BG', 'A1CF', 'A2M', 'A2M-AS1', 'A2ML1-AS1', 'A3GALT2', 'A4GALT', 'A4GNT', 'AAAS', 'AADAC', 'AADACL2', 'AADACL3', 'AADACL4', 'AADAT', 'AAED1', 'AAMDC', 'AAMP', 'AANAT', 'AAR2', 'AARD', 'AARS', 'AASDHPPT', 'AASS', 'AATBC', 'AB015752.1', 'ABCA12', 'ABCA6', 'ABCA7', 'ABCA8', 'ABCA9-AS1', 'ABCB10', 'ABCB11', 'ABCB5', 'ABCB6', 'ABCB7', 'ABCC11', 'ABCC12', 'ABCC2', 'ABCC5-AS1', 'ABCC6', 'ABCC9', 'ABCD1', 'ABCD2', 'ABCD3', 'ABCE1', 'ABCF1', 'ABCF2', 'ABCF2-1', 'ABCF3', 'ABCG5', 'ABHD10', 'ABHD11', 'ABHD12B', 'ABHD13', 'ABHD14A', 'ABHD14B', 'ABHD15', 'ABHD15-AS1', 'ABHD16A', 'ABHD16B', 'ABHD17A', 'ABHD2', 'ABHD4', 'ABHD5', 'ABI1', 'ABI2', 'ABI3', 'ABI3BP', 'ABLIM3', 'ABRA', 'ABRACL', 'ABRAXAS1', 'ABT1', 'ABTB1', 'AC000032.1', 'AC000035.1', 'AC000036.1', 'AC000058.1', 'AC000061.1', 'AC000067.1', 'AC000068.1', 'AC000068.2', 'AC000068.3', 'AC000093.1', 'AC000099.1', 'AC000123.1', 'AC000124.1', 'AC000372.1', 'AC000403.1', 'AC001226.1', 'AC002056.2', 'AC002064.1', 'AC002064.2',

In [88]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [89]:
adata

AnnData object with n_obs × n_vars = 19244 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_id

In [90]:
# here we subset to HVGs, not accounting for sample batch here - it breaks the HVG finding (not enough batch representation?)
sc.pp.highly_variable_genes(adata, min_mean=0.0125, max_mean=3, min_disp=0.5,
                           subset=True)

In [91]:
adata

AnnData object with n_obs × n_vars = 19244 × 1528
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_id

#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [92]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 19244 cells, 1528 vars, 1 batches,
         1 labels, and 0 proteins. Also registered 1 extra categorical covariates and 0 extra
         continuous covariates.                                                              
INFO     Please do not further modify adata until model is trained.                          


### 14.11.2021 Running scVI after:

- removing soupy genes as per LF approach (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell)

In [93]:
# this one is without soupy gene removal

models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

n_latent_values = [9]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 9


In [94]:
# without soupy gene filtering and with CC-assoc gene filtering

latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_T_compartment_with_LF_gene_filter_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 9
Epoch 400/400: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 400/400 [11:10<00:00,  1.68s/it, loss=139, v_num=1]


# Running on only Myeloid compartment


Subsetted by unbiased clusteing of the manifold with all cell states as calculated above with n_latent=

In [95]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [96]:
# reading IDs of final cells to keep (after also excluding doublets by GEX, done in notebook M3)
nodoublet_cell_IDs = pd.read_csv(save_path + 'selected_droplets_no_doublets_in_M1_prelim_analysis.csv', index_col=0)
nodoublet_cell_IDs

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AAACGGGCATTGGCGC-1_FCA7167219           1941        FCA7167219   
AAACGGGTCGCGATCG-1_FCA7167219           1246        FCA7167219   
AAAGATGAGCAATATG-1_FCA7167219           1516        FCA7167219   
AAAGATGAGTTCGCGC-1_FCA7167219           2099        FCA7167219   
AAAGATGCATGTCGAT-1_FCA7167219           1636        FCA7167219   
...                                      ...               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920     2409  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920     3116  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AAACGGGCATTGGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAACGGGTCGCGATCG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGCAATATG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGTTCGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGCATGTCGAT-1_FCA7167219        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AAACGGGCATTGGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAACGGGTCGCGATCG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGCAATATG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGTTCGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGCATGTCGAT-1_FCA7167219                     decidua_immune   13_PCW   
...                                                          ...      ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AAACGGGCATTGGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAACGGGTCGCGATCG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGCAATATG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGTTCGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGCATGTCGAT-1_FCA7167219           6          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AAACGGGCATTGGCGC-1_FCA7167219                                        1      0   
AAACGGGTCGCGATCG-1_FCA7167219                                        1      0   
AAAGATGAGCAATATG-1_FCA7167219                                        1      0   
AAAGATGAGTTCGCGC-1_FCA7167219                                        1      0   
AAAGATGCATG

In [97]:
# subsetting the adata object to final cells
adata = adata[list(nodoublet_cell_IDs.index), :].copy()
adata

AnnData object with n_obs × n_vars = 378558 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feature_types-1

In [98]:
# adding metadata
for col in nodoublet_cell_IDs.columns:
    print(col)
    adata.obs[col] = nodoublet_cell_IDs.loc[adata.obs_names,col]

n_genes
sample
technology
tissue
dev_age
donor
dataset
run
number_of_individuals_multiplexed
batch
percent_mito
n_counts
scrublet_score
scrublet_cluster_score
bh_pval
is_doublet
celltype_predictions
probabilities
barcode_sample_copy
souporcell_assignment
inter_ind_doublet
S_score
G2M_score
phase
origin_M_F
is_doublet_0.05
is_doublet_0.01


In [99]:
# excluding soupy genes as per notebook M2

# gene stats for cells
gene_stats_sc = pd.read_csv(save_path + 'gene_filter_cells_upd_20211111.csv', index_col=0)

# gene stats for nuclei
gene_stats_sn = pd.read_csv(save_path + 'gene_filter_nuclei_upd_20211111.csv', index_col=0)

genes2keep_sc = list(gene_stats_sc[gene_stats_sc['Selected'] == True].index)
genes2keep_sn = list(gene_stats_sn[gene_stats_sn['Selected'] == True].index)

# overlap
genes2keep = list(set(genes2keep_sc) & set(genes2keep_sn))

print(len(genes2keep))

adata = adata[:,list(set(genes2keep) & set(adata.var_names))].copy()
adata

# cell cycle related - no need to, seems like all of those have been removed by soupy gene filter
#cleaned_up_genes_cc = pd.read_csv(save_path + '', index_col=0)

7849


AnnData object with n_obs × n_vars = 378558 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature

In [100]:
# subsetting to only trophoblast according to coarse annotation done in notebook M4
annot_coarse = pd.read_csv(save_path + 'obs_table_with_coarse_annot_from_M4_notebook_all_cell_states.csv',
                          index_col=0)
adata.obs['annot_coarse'] = annot_coarse.loc[adata.obs_names,'annot_coarse']
adata.obs['annot_coarse'].value_counts()

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6,28) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


dS_uSMC        158106
Trophoblast     81704
Myeloid         43997
NK              30132
T               19244
Epithelial      18222
Endothelial     12689
fF              12633
PV               1831
Name: annot_coarse, dtype: int64

In [101]:
adata = adata[adata.obs['annot_coarse'] == 'Myeloid'].copy()

In [102]:
adata

AnnData object with n_obs × n_vars = 43997 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_id

In [104]:
# CC-assoc gene filtering here

cleaned_up_genes = pd.read_csv(save_path + 'cleaned_up_genes_in_S5_notebook_Myeloid_20211114.csv', index_col=0)

adata = adata[:,cleaned_up_genes.index].copy()
adata

# optimal n_PCs = 9 here

KeyError: "Values ['A1BG', 'A1CF', 'A2M', 'A2M-AS1', 'A2ML1-AS1', 'A3GALT2', 'A4GALT', 'A4GNT', 'AAAS', 'AADAC', 'AADACL2', 'AADACL3', 'AADACL4', 'AADAT', 'AAED1', 'AAMDC', 'AAMP', 'AANAT', 'AAR2', 'AARD', 'AARS', 'AASDHPPT', 'AASS', 'AATBC', 'AB015752.1', 'ABCA12', 'ABCA6', 'ABCA7', 'ABCA8', 'ABCA9-AS1', 'ABCB10', 'ABCB11', 'ABCB5', 'ABCB6', 'ABCB7', 'ABCC11', 'ABCC12', 'ABCC2', 'ABCC5-AS1', 'ABCC6', 'ABCC9', 'ABCD1', 'ABCD2', 'ABCD3', 'ABCE1', 'ABCF1', 'ABCF2', 'ABCF2-1', 'ABCF3', 'ABCG5', 'ABHD10', 'ABHD11', 'ABHD12B', 'ABHD13', 'ABHD14A', 'ABHD14B', 'ABHD15', 'ABHD15-AS1', 'ABHD16A', 'ABHD16B', 'ABHD17A', 'ABHD2', 'ABHD4', 'ABHD5', 'ABI1', 'ABI2', 'ABI3', 'ABI3BP', 'ABLIM3', 'ABRA', 'ABRACL', 'ABRAXAS1', 'ABT1', 'ABTB1', 'AC000032.1', 'AC000035.1', 'AC000036.1', 'AC000058.1', 'AC000061.1', 'AC000067.1', 'AC000068.1', 'AC000068.2', 'AC000068.3', 'AC000093.1', 'AC000099.1', 'AC000123.1', 'AC000124.1', 'AC000372.1', 'AC000403.1', 'AC001226.1', 'AC002056.2', 'AC002064.1', 'AC002064.2',

In [105]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [106]:
adata

AnnData object with n_obs × n_vars = 43997 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_id

In [107]:
# here we subset to HVGs, not accounting for sample batch here - it breaks the HVG finding (not enough batch representation?)
sc.pp.highly_variable_genes(adata, min_mean=0.0125, max_mean=3, min_disp=0.5,
                           subset=True)

In [108]:
adata

AnnData object with n_obs × n_vars = 43997 × 1981
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_id

#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [109]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 43997 cells, 1981 vars, 1 batches,
         1 labels, and 0 proteins. Also registered 1 extra categorical covariates and 0 extra
         continuous covariates.                                                              
INFO     Please do not further modify adata until model is trained.                          


### 14.11.2021 Running scVI after:

- removing soupy genes as per LF approach (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell)

In [110]:
# this one is without soupy gene removal

models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

n_latent_values = [9]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 9


In [111]:
# without soupy gene filtering and with CC-assoc gene filtering

latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_Myeloid_compartment_with_LF_gene_filter_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 9
Epoch 182/182: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 182/182 [11:44<00:00,  3.87s/it, loss=398, v_num=1]


# Running on only Endothelial compartment


Subsetted by unbiased clusteing of the manifold with all cell states as calculated above with n_latent=

In [112]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [113]:
# reading IDs of final cells to keep (after also excluding doublets by GEX, done in notebook M3)
nodoublet_cell_IDs = pd.read_csv(save_path + 'selected_droplets_no_doublets_in_M1_prelim_analysis.csv', index_col=0)
nodoublet_cell_IDs

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AAACGGGCATTGGCGC-1_FCA7167219           1941        FCA7167219   
AAACGGGTCGCGATCG-1_FCA7167219           1246        FCA7167219   
AAAGATGAGCAATATG-1_FCA7167219           1516        FCA7167219   
AAAGATGAGTTCGCGC-1_FCA7167219           2099        FCA7167219   
AAAGATGCATGTCGAT-1_FCA7167219           1636        FCA7167219   
...                                      ...               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920     2409  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920     3116  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AAACGGGCATTGGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAACGGGTCGCGATCG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGCAATATG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGTTCGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGCATGTCGAT-1_FCA7167219        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AAACGGGCATTGGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAACGGGTCGCGATCG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGCAATATG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGTTCGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGCATGTCGAT-1_FCA7167219                     decidua_immune   13_PCW   
...                                                          ...      ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AAACGGGCATTGGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAACGGGTCGCGATCG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGCAATATG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGTTCGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGCATGTCGAT-1_FCA7167219           6          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AAACGGGCATTGGCGC-1_FCA7167219                                        1      0   
AAACGGGTCGCGATCG-1_FCA7167219                                        1      0   
AAAGATGAGCAATATG-1_FCA7167219                                        1      0   
AAAGATGAGTTCGCGC-1_FCA7167219                                        1      0   
AAAGATGCATG

In [114]:
# subsetting the adata object to final cells
adata = adata[list(nodoublet_cell_IDs.index), :].copy()
adata

AnnData object with n_obs × n_vars = 378558 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feature_types-1

In [115]:
# adding metadata
for col in nodoublet_cell_IDs.columns:
    print(col)
    adata.obs[col] = nodoublet_cell_IDs.loc[adata.obs_names,col]

n_genes
sample
technology
tissue
dev_age
donor
dataset
run
number_of_individuals_multiplexed
batch
percent_mito
n_counts
scrublet_score
scrublet_cluster_score
bh_pval
is_doublet
celltype_predictions
probabilities
barcode_sample_copy
souporcell_assignment
inter_ind_doublet
S_score
G2M_score
phase
origin_M_F
is_doublet_0.05
is_doublet_0.01


In [116]:
# excluding soupy genes as per notebook M2

# gene stats for cells
gene_stats_sc = pd.read_csv(save_path + 'gene_filter_cells_upd_20211111.csv', index_col=0)

# gene stats for nuclei
gene_stats_sn = pd.read_csv(save_path + 'gene_filter_nuclei_upd_20211111.csv', index_col=0)

genes2keep_sc = list(gene_stats_sc[gene_stats_sc['Selected'] == True].index)
genes2keep_sn = list(gene_stats_sn[gene_stats_sn['Selected'] == True].index)

# overlap
genes2keep = list(set(genes2keep_sc) & set(genes2keep_sn))

print(len(genes2keep))

adata = adata[:,list(set(genes2keep) & set(adata.var_names))].copy()
adata

# cell cycle related - no need to, seems like all of those have been removed by soupy gene filter
#cleaned_up_genes_cc = pd.read_csv(save_path + '', index_col=0)

7849


AnnData object with n_obs × n_vars = 378558 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature

In [117]:
# subsetting to only trophoblast according to coarse annotation done in notebook M4
annot_coarse = pd.read_csv(save_path + 'obs_table_with_coarse_annot_from_M4_notebook_all_cell_states.csv',
                          index_col=0)
adata.obs['annot_coarse'] = annot_coarse.loc[adata.obs_names,'annot_coarse']
adata.obs['annot_coarse'].value_counts()

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6,28) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


dS_uSMC        158106
Trophoblast     81704
Myeloid         43997
NK              30132
T               19244
Epithelial      18222
Endothelial     12689
fF              12633
PV               1831
Name: annot_coarse, dtype: int64

In [118]:
adata = adata[adata.obs['annot_coarse'] == 'Endothelial'].copy()

In [119]:
adata

AnnData object with n_obs × n_vars = 12689 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_id

In [120]:
# CC-assoc gene filtering here

cleaned_up_genes = pd.read_csv(save_path + 'cleaned_up_genes_in_S6_notebook_Endothelial_20211114.csv', index_col=0)

adata = adata[:,cleaned_up_genes.index].copy()
adata

# optimal n_PCs = 7 here

KeyError: "Values ['A1BG', 'A1CF', 'A2M', 'A2M-AS1', 'A2ML1-AS1', 'A3GALT2', 'A4GALT', 'A4GNT', 'AAAS', 'AADAC', 'AADACL2', 'AADACL3', 'AADACL4', 'AADAT', 'AAED1', 'AAMDC', 'AAMP', 'AANAT', 'AAR2', 'AARD', 'AARS', 'AASDHPPT', 'AASS', 'AATBC', 'AB015752.1', 'ABCA12', 'ABCA6', 'ABCA7', 'ABCA8', 'ABCB10', 'ABCB11', 'ABCB5', 'ABCB6', 'ABCB7', 'ABCC11', 'ABCC12', 'ABCC2', 'ABCC5-AS1', 'ABCC6', 'ABCC9', 'ABCD1', 'ABCD2', 'ABCD3', 'ABCE1', 'ABCF1', 'ABCF2', 'ABCF2-1', 'ABCF3', 'ABCG5', 'ABHD10', 'ABHD11', 'ABHD12B', 'ABHD13', 'ABHD14A', 'ABHD14B', 'ABHD15', 'ABHD15-AS1', 'ABHD16A', 'ABHD16B', 'ABHD17A', 'ABHD2', 'ABHD4', 'ABHD5', 'ABI1', 'ABI2', 'ABI3', 'ABI3BP', 'ABLIM3', 'ABRA', 'ABRACL', 'ABRAXAS1', 'ABT1', 'ABTB1', 'AC000032.1', 'AC000035.1', 'AC000036.1', 'AC000058.1', 'AC000061.1', 'AC000067.1', 'AC000068.1', 'AC000068.2', 'AC000068.3', 'AC000093.1', 'AC000099.1', 'AC000123.1', 'AC000124.1', 'AC000372.1', 'AC000403.1', 'AC001226.1', 'AC002056.2', 'AC002064.1', 'AC002064.2', 'AC002066.1'

In [121]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [122]:
adata

AnnData object with n_obs × n_vars = 12689 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_id

In [123]:
# here we subset to HVGs, not accounting for sample batch here - it breaks the HVG finding (not enough batch representation?)
sc.pp.highly_variable_genes(adata, min_mean=0.0125, max_mean=3, min_disp=0.5,
                           subset=True)

In [124]:
adata

AnnData object with n_obs × n_vars = 12689 × 2001
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_id

#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [125]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 12689 cells, 2001 vars, 1 batches,
         1 labels, and 0 proteins. Also registered 1 extra categorical covariates and 0 extra
         continuous covariates.                                                              
INFO     Please do not further modify adata until model is trained.                          


### 14.11.2021 Running scVI after:

- removing soupy genes as per LF approach (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell)

In [126]:
# this one is without soupy gene removal

models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

n_latent_values = [7]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 7


In [127]:
# with soupy gene filtering

latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_Endothelial_compartment_with_LF_gene_filter_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 7
Epoch 400/400: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 400/400 [07:28<00:00,  1.12s/it, loss=739, v_num=1]


# Running on only Epithelial compartment


Subsetted by unbiased clusteing of the manifold with all cell states as calculated above with n_latent=

In [129]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [130]:
# reading IDs of final cells to keep (after also excluding doublets by GEX, done in notebook M3)
nodoublet_cell_IDs = pd.read_csv(save_path + 'selected_droplets_no_doublets_in_M1_prelim_analysis.csv', index_col=0)
nodoublet_cell_IDs

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AAACGGGCATTGGCGC-1_FCA7167219           1941        FCA7167219   
AAACGGGTCGCGATCG-1_FCA7167219           1246        FCA7167219   
AAAGATGAGCAATATG-1_FCA7167219           1516        FCA7167219   
AAAGATGAGTTCGCGC-1_FCA7167219           2099        FCA7167219   
AAAGATGCATGTCGAT-1_FCA7167219           1636        FCA7167219   
...                                      ...               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920     2409  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920     3116  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AAACGGGCATTGGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAACGGGTCGCGATCG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGCAATATG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGTTCGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGCATGTCGAT-1_FCA7167219        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AAACGGGCATTGGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAACGGGTCGCGATCG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGCAATATG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGTTCGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGCATGTCGAT-1_FCA7167219                     decidua_immune   13_PCW   
...                                                          ...      ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AAACGGGCATTGGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAACGGGTCGCGATCG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGCAATATG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGTTCGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGCATGTCGAT-1_FCA7167219           6          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AAACGGGCATTGGCGC-1_FCA7167219                                        1      0   
AAACGGGTCGCGATCG-1_FCA7167219                                        1      0   
AAAGATGAGCAATATG-1_FCA7167219                                        1      0   
AAAGATGAGTTCGCGC-1_FCA7167219                                        1      0   
AAAGATGCATG

In [131]:
# subsetting the adata object to final cells
adata = adata[list(nodoublet_cell_IDs.index), :].copy()
adata

AnnData object with n_obs × n_vars = 378558 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feature_types-1

In [132]:
# adding metadata
for col in nodoublet_cell_IDs.columns:
    print(col)
    adata.obs[col] = nodoublet_cell_IDs.loc[adata.obs_names,col]

n_genes
sample
technology
tissue
dev_age
donor
dataset
run
number_of_individuals_multiplexed
batch
percent_mito
n_counts
scrublet_score
scrublet_cluster_score
bh_pval
is_doublet
celltype_predictions
probabilities
barcode_sample_copy
souporcell_assignment
inter_ind_doublet
S_score
G2M_score
phase
origin_M_F
is_doublet_0.05
is_doublet_0.01


In [133]:
# excluding soupy genes as per notebook M2

# gene stats for cells
gene_stats_sc = pd.read_csv(save_path + 'gene_filter_cells_upd_20211111.csv', index_col=0)

# gene stats for nuclei
gene_stats_sn = pd.read_csv(save_path + 'gene_filter_nuclei_upd_20211111.csv', index_col=0)

genes2keep_sc = list(gene_stats_sc[gene_stats_sc['Selected'] == True].index)
genes2keep_sn = list(gene_stats_sn[gene_stats_sn['Selected'] == True].index)

# overlap
genes2keep = list(set(genes2keep_sc) & set(genes2keep_sn))

print(len(genes2keep))

adata = adata[:,list(set(genes2keep) & set(adata.var_names))].copy()
adata

# cell cycle related - no need to, seems like all of those have been removed by soupy gene filter
#cleaned_up_genes_cc = pd.read_csv(save_path + '', index_col=0)

7849


AnnData object with n_obs × n_vars = 378558 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature

In [134]:
# subsetting to only trophoblast according to coarse annotation done in notebook M4
annot_coarse = pd.read_csv(save_path + 'obs_table_with_coarse_annot_from_M4_notebook_all_cell_states.csv',
                          index_col=0)
adata.obs['annot_coarse'] = annot_coarse.loc[adata.obs_names,'annot_coarse']
adata.obs['annot_coarse'].value_counts()

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6,28) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


dS_uSMC        158106
Trophoblast     81704
Myeloid         43997
NK              30132
T               19244
Epithelial      18222
Endothelial     12689
fF              12633
PV               1831
Name: annot_coarse, dtype: int64

In [135]:
adata = adata[adata.obs['annot_coarse'] == 'Epithelial'].copy()

In [136]:
adata

AnnData object with n_obs × n_vars = 18222 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_id

In [138]:
# CC-assoc gene filtering here

cleaned_up_genes = pd.read_csv(save_path + 'cleaned_up_genes_in_S7_notebook_Epithelial_20211114.csv', index_col=0)

adata = adata[:,cleaned_up_genes.index].copy()
adata

# optimal n_PCs = 16 here

KeyError: "Values ['A1BG', 'A1CF', 'A2M', 'A2M-AS1', 'A2ML1-AS1', 'A3GALT2', 'A4GALT', 'A4GNT', 'AAAS', 'AADAC', 'AADACL2', 'AADACL3', 'AADACL4', 'AADAT', 'AAED1', 'AAMDC', 'AAMP', 'AANAT', 'AAR2', 'AARD', 'AARS', 'AASDHPPT', 'AASS', 'AATBC', 'AB015752.1', 'ABCA12', 'ABCA6', 'ABCA8', 'ABCA9-AS1', 'ABCB10', 'ABCB11', 'ABCB5', 'ABCB6', 'ABCB7', 'ABCC11', 'ABCC12', 'ABCC2', 'ABCC5-AS1', 'ABCC6', 'ABCC9', 'ABCD1', 'ABCD2', 'ABCD3', 'ABCE1', 'ABCF1', 'ABCF2', 'ABCF2-1', 'ABCF3', 'ABCG5', 'ABHD10', 'ABHD11', 'ABHD12B', 'ABHD13', 'ABHD14A', 'ABHD14B', 'ABHD15', 'ABHD15-AS1', 'ABHD16A', 'ABHD16B', 'ABHD17A', 'ABHD2', 'ABHD4', 'ABHD5', 'ABI1', 'ABI2', 'ABI3', 'ABI3BP', 'ABLIM3', 'ABRA', 'ABRACL', 'ABRAXAS1', 'ABT1', 'ABTB1', 'AC000032.1', 'AC000035.1', 'AC000036.1', 'AC000058.1', 'AC000061.1', 'AC000067.1', 'AC000068.1', 'AC000068.2', 'AC000068.3', 'AC000093.1', 'AC000099.1', 'AC000123.1', 'AC000124.1', 'AC000372.1', 'AC000403.1', 'AC001226.1', 'AC002056.2', 'AC002064.1', 'AC002064.2', 'AC00206

In [139]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [140]:
adata

AnnData object with n_obs × n_vars = 18222 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_id

In [141]:
# here we subset to HVGs, not accounting for sample batch here - it breaks the HVG finding (not enough batch representation?)
sc.pp.highly_variable_genes(adata, min_mean=0.0125, max_mean=3, min_disp=0.5,
                           subset=True)

In [142]:
adata

AnnData object with n_obs × n_vars = 18222 × 1837
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_id

#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [143]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 18222 cells, 1837 vars, 1 batches,
         1 labels, and 0 proteins. Also registered 1 extra categorical covariates and 0 extra
         continuous covariates.                                                              
INFO     Please do not further modify adata until model is trained.                          


### 14.11.2021 Running scVI after:

- removing soupy genes as per LF approach (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell)

In [144]:
# this one is without soupy gene removal

models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

n_latent_values = [16]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 16


In [145]:
# without soupy gene filtering and with CC-assoc gene filtering

latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_Epithelial_compartment_with_LF_gene_filter_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 16
Epoch 400/400: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 400/400 [10:47<00:00,  1.62s/it, loss=551, v_num=1]


# Running on only fF compartment


Subsetted by unbiased clusteing of the manifold with all cell states as calculated above with n_latent=

In [146]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [147]:
# reading IDs of final cells to keep (after also excluding doublets by GEX, done in notebook M3)
nodoublet_cell_IDs = pd.read_csv(save_path + 'selected_droplets_no_doublets_in_M1_prelim_analysis.csv', index_col=0)
nodoublet_cell_IDs

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AAACGGGCATTGGCGC-1_FCA7167219           1941        FCA7167219   
AAACGGGTCGCGATCG-1_FCA7167219           1246        FCA7167219   
AAAGATGAGCAATATG-1_FCA7167219           1516        FCA7167219   
AAAGATGAGTTCGCGC-1_FCA7167219           2099        FCA7167219   
AAAGATGCATGTCGAT-1_FCA7167219           1636        FCA7167219   
...                                      ...               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920     2409  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920     3116  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AAACGGGCATTGGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAACGGGTCGCGATCG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGCAATATG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGTTCGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGCATGTCGAT-1_FCA7167219        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AAACGGGCATTGGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAACGGGTCGCGATCG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGCAATATG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGTTCGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGCATGTCGAT-1_FCA7167219                     decidua_immune   13_PCW   
...                                                          ...      ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AAACGGGCATTGGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAACGGGTCGCGATCG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGCAATATG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGTTCGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGCATGTCGAT-1_FCA7167219           6          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AAACGGGCATTGGCGC-1_FCA7167219                                        1      0   
AAACGGGTCGCGATCG-1_FCA7167219                                        1      0   
AAAGATGAGCAATATG-1_FCA7167219                                        1      0   
AAAGATGAGTTCGCGC-1_FCA7167219                                        1      0   
AAAGATGCATG

In [148]:
# subsetting the adata object to final cells
adata = adata[list(nodoublet_cell_IDs.index), :].copy()
adata

AnnData object with n_obs × n_vars = 378558 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feature_types-1

In [149]:
# adding metadata
for col in nodoublet_cell_IDs.columns:
    print(col)
    adata.obs[col] = nodoublet_cell_IDs.loc[adata.obs_names,col]

n_genes
sample
technology
tissue
dev_age
donor
dataset
run
number_of_individuals_multiplexed
batch
percent_mito
n_counts
scrublet_score
scrublet_cluster_score
bh_pval
is_doublet
celltype_predictions
probabilities
barcode_sample_copy
souporcell_assignment
inter_ind_doublet
S_score
G2M_score
phase
origin_M_F
is_doublet_0.05
is_doublet_0.01


In [150]:
# excluding soupy genes as per notebook M2

# gene stats for cells
gene_stats_sc = pd.read_csv(save_path + 'gene_filter_cells_upd_20211111.csv', index_col=0)

# gene stats for nuclei
gene_stats_sn = pd.read_csv(save_path + 'gene_filter_nuclei_upd_20211111.csv', index_col=0)

genes2keep_sc = list(gene_stats_sc[gene_stats_sc['Selected'] == True].index)
genes2keep_sn = list(gene_stats_sn[gene_stats_sn['Selected'] == True].index)

# overlap
genes2keep = list(set(genes2keep_sc) & set(genes2keep_sn))

print(len(genes2keep))

adata = adata[:,list(set(genes2keep) & set(adata.var_names))].copy()
adata

# cell cycle related - no need to, seems like all of those have been removed by soupy gene filter
#cleaned_up_genes_cc = pd.read_csv(save_path + '', index_col=0)

7849


AnnData object with n_obs × n_vars = 378558 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature

In [151]:
# subsetting to only trophoblast according to coarse annotation done in notebook M4
annot_coarse = pd.read_csv(save_path + 'obs_table_with_coarse_annot_from_M4_notebook_all_cell_states.csv',
                          index_col=0)
adata.obs['annot_coarse'] = annot_coarse.loc[adata.obs_names,'annot_coarse']
adata.obs['annot_coarse'].value_counts()

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6,28) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


dS_uSMC        158106
Trophoblast     81704
Myeloid         43997
NK              30132
T               19244
Epithelial      18222
Endothelial     12689
fF              12633
PV               1831
Name: annot_coarse, dtype: int64

In [152]:
adata = adata[adata.obs['annot_coarse'] == 'fF'].copy()

In [153]:
adata

AnnData object with n_obs × n_vars = 12633 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_id

In [155]:
# CC-assoc gene filtering here

cleaned_up_genes = pd.read_csv(save_path + 'cleaned_up_genes_in_S8_notebook_fF_20211114.csv', index_col=0)

adata = adata[:,cleaned_up_genes.index].copy()
adata

# optimal n_PCs = 7 here

KeyError: "Values ['A1BG', 'A1CF', 'A2M', 'A2M-AS1', 'A2ML1-AS1', 'A3GALT2', 'A4GALT', 'A4GNT', 'AAAS', 'AADAC', 'AADACL2', 'AADACL3', 'AADACL4', 'AADAT', 'AAED1', 'AAMDC', 'AAMP', 'AANAT', 'AAR2', 'AARD', 'AARS', 'AASDHPPT', 'AASS', 'AATBC', 'AB015752.1', 'ABCA12', 'ABCA6', 'ABCA7', 'ABCA8', 'ABCA9-AS1', 'ABCB10', 'ABCB11', 'ABCB5', 'ABCB6', 'ABCB7', 'ABCC11', 'ABCC12', 'ABCC2', 'ABCC5-AS1', 'ABCC6', 'ABCC9', 'ABCD1', 'ABCD2', 'ABCD3', 'ABCE1', 'ABCF1', 'ABCF2', 'ABCF2-1', 'ABCF3', 'ABCG5', 'ABHD10', 'ABHD11', 'ABHD12B', 'ABHD13', 'ABHD14A', 'ABHD14B', 'ABHD15', 'ABHD15-AS1', 'ABHD16A', 'ABHD16B', 'ABHD17A', 'ABHD2', 'ABHD4', 'ABHD5', 'ABI1', 'ABI2', 'ABI3', 'ABI3BP', 'ABLIM3', 'ABRA', 'ABRACL', 'ABRAXAS1', 'ABT1', 'ABTB1', 'AC000032.1', 'AC000035.1', 'AC000036.1', 'AC000058.1', 'AC000061.1', 'AC000067.1', 'AC000068.1', 'AC000068.2', 'AC000068.3', 'AC000093.1', 'AC000099.1', 'AC000123.1', 'AC000124.1', 'AC000372.1', 'AC000403.1', 'AC001226.1', 'AC002056.2', 'AC002064.1', 'AC002064.2',

In [157]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [158]:
adata

AnnData object with n_obs × n_vars = 12633 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_id

In [159]:
# here we subset to HVGs, not accounting for sample batch here - it breaks the HVG finding (not enough batch representation?)
sc.pp.highly_variable_genes(adata, min_mean=0.0125, max_mean=3, min_disp=0.5,
                           subset=True)

In [160]:
adata

AnnData object with n_obs × n_vars = 12633 × 1743
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_id

#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [161]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 12633 cells, 1743 vars, 1 batches,
         1 labels, and 0 proteins. Also registered 1 extra categorical covariates and 0 extra
         continuous covariates.                                                              
INFO     Please do not further modify adata until model is trained.                          


### 14.11.2021 Running scVI after:

- removing soupy genes as per LF approach (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell)

In [162]:
# this one is without soupy gene removal

models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

n_latent_values = [4]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 4


In [163]:
# without soupy gene filtering and with CC-assoc gene filtering

latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_fF_compartment_with_LF_gene_filter_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 4
Epoch 400/400: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 400/400 [07:26<00:00,  1.12s/it, loss=476, v_num=1]


# Running on only PV compartment


Subsetted by unbiased clusteing of the manifold with all cell states as calculated above with n_latent=

In [164]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [165]:
# reading IDs of final cells to keep (after also excluding doublets by GEX, done in notebook M3)
nodoublet_cell_IDs = pd.read_csv(save_path + 'selected_droplets_no_doublets_in_M1_prelim_analysis.csv', index_col=0)
nodoublet_cell_IDs

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AAACGGGCATTGGCGC-1_FCA7167219           1941        FCA7167219   
AAACGGGTCGCGATCG-1_FCA7167219           1246        FCA7167219   
AAAGATGAGCAATATG-1_FCA7167219           1516        FCA7167219   
AAAGATGAGTTCGCGC-1_FCA7167219           2099        FCA7167219   
AAAGATGCATGTCGAT-1_FCA7167219           1636        FCA7167219   
...                                      ...               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920     2409  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920     3116  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AAACGGGCATTGGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAACGGGTCGCGATCG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGCAATATG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGTTCGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGCATGTCGAT-1_FCA7167219        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AAACGGGCATTGGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAACGGGTCGCGATCG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGCAATATG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGTTCGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGCATGTCGAT-1_FCA7167219                     decidua_immune   13_PCW   
...                                                          ...      ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AAACGGGCATTGGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAACGGGTCGCGATCG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGCAATATG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGTTCGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGCATGTCGAT-1_FCA7167219           6          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AAACGGGCATTGGCGC-1_FCA7167219                                        1      0   
AAACGGGTCGCGATCG-1_FCA7167219                                        1      0   
AAAGATGAGCAATATG-1_FCA7167219                                        1      0   
AAAGATGAGTTCGCGC-1_FCA7167219                                        1      0   
AAAGATGCATG

In [166]:
# subsetting the adata object to final cells
adata = adata[list(nodoublet_cell_IDs.index), :].copy()
adata

AnnData object with n_obs × n_vars = 378558 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feature_types-1

In [167]:
# adding metadata
for col in nodoublet_cell_IDs.columns:
    print(col)
    adata.obs[col] = nodoublet_cell_IDs.loc[adata.obs_names,col]

n_genes
sample
technology
tissue
dev_age
donor
dataset
run
number_of_individuals_multiplexed
batch
percent_mito
n_counts
scrublet_score
scrublet_cluster_score
bh_pval
is_doublet
celltype_predictions
probabilities
barcode_sample_copy
souporcell_assignment
inter_ind_doublet
S_score
G2M_score
phase
origin_M_F
is_doublet_0.05
is_doublet_0.01


In [168]:
# excluding soupy genes as per notebook M2

# gene stats for cells
gene_stats_sc = pd.read_csv(save_path + 'gene_filter_cells_upd_20211111.csv', index_col=0)

# gene stats for nuclei
gene_stats_sn = pd.read_csv(save_path + 'gene_filter_nuclei_upd_20211111.csv', index_col=0)

genes2keep_sc = list(gene_stats_sc[gene_stats_sc['Selected'] == True].index)
genes2keep_sn = list(gene_stats_sn[gene_stats_sn['Selected'] == True].index)

# overlap
genes2keep = list(set(genes2keep_sc) & set(genes2keep_sn))

print(len(genes2keep))

adata = adata[:,list(set(genes2keep) & set(adata.var_names))].copy()
adata

# cell cycle related - no need to, seems like all of those have been removed by soupy gene filter
#cleaned_up_genes_cc = pd.read_csv(save_path + '', index_col=0)

7849


AnnData object with n_obs × n_vars = 378558 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature

In [169]:
# subsetting to only trophoblast according to coarse annotation done in notebook M4
annot_coarse = pd.read_csv(save_path + 'obs_table_with_coarse_annot_from_M4_notebook_all_cell_states.csv',
                          index_col=0)
adata.obs['annot_coarse'] = annot_coarse.loc[adata.obs_names,'annot_coarse']
adata.obs['annot_coarse'].value_counts()

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6,28) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


dS_uSMC        158106
Trophoblast     81704
Myeloid         43997
NK              30132
T               19244
Epithelial      18222
Endothelial     12689
fF              12633
PV               1831
Name: annot_coarse, dtype: int64

In [170]:
adata = adata[adata.obs['annot_coarse'] == 'PV'].copy()

In [171]:
adata

AnnData object with n_obs × n_vars = 1831 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids

In [172]:
# CC-assoc gene filtering here

cleaned_up_genes = pd.read_csv(save_path + 'cleaned_up_genes_in_S9_notebook_PV_20211114.csv', index_col=0)

adata = adata[:,cleaned_up_genes.index].copy()
adata

# optimal n_PCs = 7 here

KeyError: "Values ['A1BG', 'A1CF', 'A2M', 'A2M-AS1', 'A2ML1-AS1', 'A3GALT2', 'A4GALT', 'A4GNT', 'AAAS', 'AADAC', 'AADACL2', 'AADACL3', 'AADACL4', 'AADAT', 'AAED1', 'AAMDC', 'AAMP', 'AANAT', 'AAR2', 'AARD', 'AARS', 'AASDHPPT', 'AASS', 'AATBC', 'AB015752.1', 'ABCA12', 'ABCA6', 'ABCA7', 'ABCA8', 'ABCA9-AS1', 'ABCB10', 'ABCB11', 'ABCB5', 'ABCB6', 'ABCB7', 'ABCC11', 'ABCC12', 'ABCC2', 'ABCC5-AS1', 'ABCC6', 'ABCC9', 'ABCD1', 'ABCD2', 'ABCD3', 'ABCE1', 'ABCF1', 'ABCF2', 'ABCF2-1', 'ABCF3', 'ABCG5', 'ABHD10', 'ABHD11', 'ABHD12B', 'ABHD13', 'ABHD14A', 'ABHD14B', 'ABHD15', 'ABHD15-AS1', 'ABHD16A', 'ABHD16B', 'ABHD17A', 'ABHD2', 'ABHD4', 'ABHD5', 'ABI1', 'ABI2', 'ABI3', 'ABI3BP', 'ABLIM3', 'ABRA', 'ABRACL', 'ABRAXAS1', 'ABT1', 'ABTB1', 'AC000032.1', 'AC000035.1', 'AC000036.1', 'AC000058.1', 'AC000061.1', 'AC000067.1', 'AC000068.1', 'AC000068.2', 'AC000068.3', 'AC000093.1', 'AC000099.1', 'AC000123.1', 'AC000124.1', 'AC000372.1', 'AC000403.1', 'AC001226.1', 'AC002056.2', 'AC002064.1', 'AC002064.2',

In [173]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [174]:
adata

AnnData object with n_obs × n_vars = 1831 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids

In [175]:
# here we subset to HVGs, not accounting for sample batch here - it breaks the HVG finding (not enough batch representation?)
sc.pp.highly_variable_genes(adata, min_mean=0.0125, max_mean=3, min_disp=0.5,
                           subset=True)

In [176]:
adata

AnnData object with n_obs × n_vars = 1831 × 1508
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_coarse'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids

#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [177]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 1831 cells, 1508 vars, 1 batches, 
         1 labels, and 0 proteins. Also registered 1 extra categorical covariates and 0 extra
         continuous covariates.                                                              
INFO     Please do not further modify adata until model is trained.                          


### 14.11.2021 Running scVI after:

- removing soupy genes as per LF approach (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell)

In [178]:
# this one is without soupy gene removal

models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

n_latent_values = [9]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 9


In [179]:
# without soupy gene filtering and with CC-assoc gene filtering

latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_PV_compartment_with_LF_gene_filter_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 9
Epoch 400/400: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 400/400 [01:07<00:00,  5.91it/s, loss=237, v_num=1]


# Running on final version of all trophoblast


Subsetted by unbiased clusteing of the manifold with all cell states as calculated above with n_latent=

In [180]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [181]:
# reading IDs of final cells to keep (after also excluding doublets by GEX, done in notebook M3)
nodoublet_cell_IDs = pd.read_csv(save_path + 'selected_droplets_no_doublets_in_M1_prelim_analysis.csv', index_col=0)
nodoublet_cell_IDs

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AAACGGGCATTGGCGC-1_FCA7167219           1941        FCA7167219   
AAACGGGTCGCGATCG-1_FCA7167219           1246        FCA7167219   
AAAGATGAGCAATATG-1_FCA7167219           1516        FCA7167219   
AAAGATGAGTTCGCGC-1_FCA7167219           2099        FCA7167219   
AAAGATGCATGTCGAT-1_FCA7167219           1636        FCA7167219   
...                                      ...               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920     2409  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920     3116  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AAACGGGCATTGGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAACGGGTCGCGATCG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGCAATATG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGTTCGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGCATGTCGAT-1_FCA7167219        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AAACGGGCATTGGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAACGGGTCGCGATCG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGCAATATG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGTTCGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGCATGTCGAT-1_FCA7167219                     decidua_immune   13_PCW   
...                                                          ...      ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AAACGGGCATTGGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAACGGGTCGCGATCG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGCAATATG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGTTCGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGCATGTCGAT-1_FCA7167219           6          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AAACGGGCATTGGCGC-1_FCA7167219                                        1      0   
AAACGGGTCGCGATCG-1_FCA7167219                                        1      0   
AAAGATGAGCAATATG-1_FCA7167219                                        1      0   
AAAGATGAGTTCGCGC-1_FCA7167219                                        1      0   
AAAGATGCATG

In [182]:
# subsetting the adata object to final cells
adata = adata[list(nodoublet_cell_IDs.index), :].copy()
adata

AnnData object with n_obs × n_vars = 378558 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feature_types-1

In [183]:
# adding metadata
for col in nodoublet_cell_IDs.columns:
    print(col)
    adata.obs[col] = nodoublet_cell_IDs.loc[adata.obs_names,col]

n_genes
sample
technology
tissue
dev_age
donor
dataset
run
number_of_individuals_multiplexed
batch
percent_mito
n_counts
scrublet_score
scrublet_cluster_score
bh_pval
is_doublet
celltype_predictions
probabilities
barcode_sample_copy
souporcell_assignment
inter_ind_doublet
S_score
G2M_score
phase
origin_M_F
is_doublet_0.05
is_doublet_0.01


In [184]:
# excluding soupy genes as per notebook M2

# gene stats for cells
gene_stats_sc = pd.read_csv(save_path + 'gene_filter_cells_upd_20211111.csv', index_col=0)

# gene stats for nuclei
gene_stats_sn = pd.read_csv(save_path + 'gene_filter_nuclei_upd_20211111.csv', index_col=0)

genes2keep_sc = list(gene_stats_sc[gene_stats_sc['Selected'] == True].index)
genes2keep_sn = list(gene_stats_sn[gene_stats_sn['Selected'] == True].index)

# overlap
genes2keep = list(set(genes2keep_sc) & set(genes2keep_sn))

print(len(genes2keep))

adata = adata[:,list(set(genes2keep) & set(adata.var_names))].copy()
adata

# cell cycle related - no need to, seems like all of those have been removed by soupy gene filter
#cleaned_up_genes_cc = pd.read_csv(save_path + '', index_col=0)

7849


AnnData object with n_obs × n_vars = 378558 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature

In [186]:
# subsetting to only final trophoblast
annot_troph = pd.read_csv(save_path + 'obs_table_all_troph_v3_prelim_annot.csv',
                          index_col=0)
adata = adata[annot_troph.index,:].copy()
adata.obs['annot_troph'] = annot_troph.loc[adata.obs_names,'annot_troph']
adata.obs['annot_troph'].value_counts()

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6,36) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


SCT           28177
VCT           23470
VCT_p          6679
EVT_1          5286
iEVT           3639
VCT_CCC        3373
EVT_2          2347
VCT_fusing     1971
rest            813
GC               72
eEVT             28
Name: annot_troph, dtype: int64

In [187]:
# disregarding 'rest' class here
adata = adata[adata.obs['annot_troph'] != 'rest'].copy()

In [188]:
adata

AnnData object with n_obs × n_vars = 75042 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_troph'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids

In [189]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [190]:
adata

AnnData object with n_obs × n_vars = 75042 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_troph'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids

In [191]:
# here we subset to HVGs, not accounting for sample batch here - it breaks the HVG finding (not enough batch representation?)
sc.pp.highly_variable_genes(adata, min_mean=0.0125, max_mean=3, min_disp=0.5,
                           subset=True)

In [192]:
adata

AnnData object with n_obs × n_vars = 75042 × 1869
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01', 'annot_troph'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids

#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [193]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 75042 cells, 1869 vars, 1 batches,
         1 labels, and 0 proteins. Also registered 1 extra categorical covariates and 0 extra
         continuous covariates.                                                              
INFO     Please do not further modify adata until model is trained.                          


### 14.11.2021 Running scVI after:

- removing soupy genes as per LF approach (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell)

In [194]:
# this one is without soupy gene removal

models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

n_latent_values = [5]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 5


In [195]:
# without soupy gene filtering and with CC-assoc gene filtering

latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211114_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_Trophoblast_compartment_v4_final_with_LF_gene_filter_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 5
Epoch 107/107: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 107/107 [11:55<00:00,  6.68s/it, loss=746, v_num=1]


# Running on all cells and nuclei - FINAL MANIFOLD


with soupy gene filtering


In [196]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [197]:
# reading IDs of final cells to keep (after also excluding doublets by GEX, done in notebook M3)
nodoublet_cell_IDs = pd.read_csv(save_path + 'selected_droplets_no_doublets_in_M1_prelim_analysis.csv', index_col=0)
nodoublet_cell_IDs

/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


n_genes            sample  \
barcode_sample                                                   
AAACGGGCATTGGCGC-1_FCA7167219           1941        FCA7167219   
AAACGGGTCGCGATCG-1_FCA7167219           1246        FCA7167219   
AAAGATGAGCAATATG-1_FCA7167219           1516        FCA7167219   
AAAGATGAGTTCGCGC-1_FCA7167219           2099        FCA7167219   
AAAGATGCATGTCGAT-1_FCA7167219           1636        FCA7167219   
...                                      ...               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920     2409  Pla_Camb10714920   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920     4129  Pla_Camb10714920   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920     3116  Pla_Camb10714920   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920     3696  Pla_Camb10714920   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920     2130  Pla_Camb10714920   

                                           technology  \
barcode_sample                                          
AAACGGGCATTGGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAACGGGTCGCGATCG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGCAATATG-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGAGTTCGCGC-1_FCA7167219        10X_3'_scRNA-seq   
AAAGATGCATGTCGAT-1_FCA7167219        10X_3'_scRNA-seq   
...                                               ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920      10X_multiome   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920      10X_multiome   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920      10X_multiome   

                                                          tissue  dev_age  \
barcode_sample                                                              
AAACGGGCATTGGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAACGGGTCGCGATCG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGCAATATG-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGAGTTCGCGC-1_FCA7167219                     decidua_immune   13_PCW   
AAAGATGCATGTCGAT-1_FCA7167219                     decidua_immune   13_PCW   
...                                                          ...      ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920  decidua_placenta_myometrium  8-9_PCW   

                                    donor               dataset  run  \
barcode_sample                                                         
AAACGGGCATTGGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAACGGGTCGCGATCG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGCAATATG-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGAGTTCGCGC-1_FCA7167219           6          Vento_Nature  NaN   
AAAGATGCATGTCGAT-1_FCA7167219           6          Vento_Nature  NaN   
...                                   ...                   ...  ...   
TTTGTGTTCGTCAAGT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTGTTCTTAGTCT-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTCACAGCG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTACTTG-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   
TTTGTTGGTTTGAGCA-1_Pla_Camb10714920   P13  Ashley_collection_sn  NaN   

                                     number_of_individuals_multiplexed  batch  \
barcode_sample                                                                  
AAACGGGCATTGGCGC-1_FCA7167219                                        1      0   
AAACGGGTCGCGATCG-1_FCA7167219                                        1      0   
AAAGATGAGCAATATG-1_FCA7167219                                        1      0   
AAAGATGAGTTCGCGC-1_FCA7167219                                        1      0   
AAAGATGCATG

In [198]:
# subsetting the adata object to final cells
adata = adata[list(nodoublet_cell_IDs.index), :].copy()
adata

AnnData object with n_obs × n_vars = 378558 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feature_types-1

In [199]:
# adding metadata
for col in nodoublet_cell_IDs.columns:
    print(col)
    adata.obs[col] = nodoublet_cell_IDs.loc[adata.obs_names,col]

n_genes
sample
technology
tissue
dev_age
donor
dataset
run
number_of_individuals_multiplexed
batch
percent_mito
n_counts
scrublet_score
scrublet_cluster_score
bh_pval
is_doublet
celltype_predictions
probabilities
barcode_sample_copy
souporcell_assignment
inter_ind_doublet
S_score
G2M_score
phase
origin_M_F
is_doublet_0.05
is_doublet_0.01


In [200]:
# excluding soupy genes as per notebook M3a-1

# gene stats for cells
gene_stats_sc = pd.read_csv(save_path + 'gene_filter_cells_upd_20211111.csv', index_col=0)

# gene stats for nuclei
gene_stats_sn = pd.read_csv(save_path + 'gene_filter_nuclei_upd_20211111.csv', index_col=0)

genes2keep_sc = list(gene_stats_sc[gene_stats_sc['Selected'] == True].index)
genes2keep_sn = list(gene_stats_sn[gene_stats_sn['Selected'] == True].index)

# overlap
genes2keep = list(set(genes2keep_sc) & set(genes2keep_sn))

print(len(genes2keep))

adata = adata[:,list(set(genes2keep) & set(adata.var_names))].copy()
adata

# cell cycle related - no need to, seems like all of those have been removed by soupy gene filter
#cleaned_up_genes_cc = pd.read_csv(save_path + '', index_col=0)

7849


AnnData object with n_obs × n_vars = 378558 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature

In [201]:
# subset to final cells and nulcei
final_annot =  pd.read_csv(save_path + 'final_annotation_all_cells_and_nulcei_20211115.csv', index_col=0)
len(final_annot)

350815

In [202]:
len(adata)

378558

In [203]:
len(set(adata.obs_names) & set(final_annot.index))

350815

In [204]:
adata = adata[final_annot.index,:].copy()
adata

AnnData object with n_obs × n_vars = 350815 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'celltype_predictions', 'probabilities', 'barcode_sample_copy', 'souporcell_assignment', 'inter_ind_doublet', 'S_score', 'G2M_score', 'phase', 'origin_M_F', 'is_doublet_0.05', 'is_doublet_0.01'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature

In [205]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [206]:
# here we subset to HVGs, accounting for donor batch
sc.pp.highly_variable_genes(
    adata,
    n_top_genes=2000,
    subset=True,
    #layer="raw_counts",
    flavor="seurat",
    batch_key="sample",
    #batch_key="donor"
)

... storing 'sample' as categorical
... storing 'technology' as categorical
... storing 'tissue' as categorical
... storing 'dev_age' as categorical
... storing 'dataset' as categorical
... storing 'celltype_predictions' as categorical
... storing 'souporcell_assignment' as categorical
... storing 'phase' as categorical
... storing 'origin_M_F' as categorical
/opt/conda/envs/scvi-singularity/lib/python3.8/site-packages/pandas/core/indexing.py:1637: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_block(indexer, value, name)


#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [207]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 350815 cells, 2000 vars, 1        
         batches, 1 labels, and 0 proteins. Also registered 1 extra categorical covariates   
         and 0 extra continuous covariates.                                                  
INFO     Please do not further modify adata until model is trained.                          


### 15.11.2021 Running scVI after:

- removing soupy genes as per LF approach (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell)
- finalisation and exclusion of all doublets (after manual zoom ins)

In [208]:
models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

# just a few values here, it was 17 PCs I used in the conventional analysis
n_latent_values = [14,20]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 14
n_latent_value 20


In [210]:
latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211111_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_CCG_removal_and_all_doublet_exclusion_by_sample_all_cells_and_nuclei_FINAL_manifold_with_LF_gene_filter_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 14
Epoch 23/23: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 23/23 [12:10<00:00, 31.75s/it, loss=704, v_num=1]


GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 20
Epoch 23/23: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 23/23 [12:07<00:00, 31.64s/it, loss=711, v_num=1]


# Running on NK + T compartments (after all cleanup, for zoomed in visualisation in Fig.1B)


Subsetted by unbiased clusteing of the manifold with all cell states as calculated above with n_latent=

In [5]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [6]:
# read in final annotations
final_annot = pd.read_csv(save_path + 'final_annotation_all_cells_and_nulcei_20211119.csv', index_col=0)

# subset to only cells in final manifold
adata = adata[final_annot.index,:].copy()
adata.obs['cell_type'] = final_annot.loc[adata.obs_names,'cell_type']
# subsetting to only NK and T cells
adata = adata[adata.obs['cell_type'].isin(['dNK1','dNK2','dNK3','ILC3','NK','T_cells','dT_cells','dT_regs'])]

In [7]:
adata

View of AnnData object with n_obs × n_vars = 47315 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'cell_type'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-1

In [8]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [9]:
adata

AnnData object with n_obs × n_vars = 47315 × 30800
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'cell_type'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'fea

In [10]:
# here we subset to HVGs, not accounting for sample batch here - it breaks the HVG finding (not enough batch representation?)
sc.pp.highly_variable_genes(adata, min_mean=0.0125, max_mean=3, min_disp=0.5,
                           subset=True)

In [11]:
adata

AnnData object with n_obs × n_vars = 47315 × 3456
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'cell_type'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feat

#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [12]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 47315 cells, 3456 vars, 1 batches,
         1 labels, and 0 proteins. Also registered 1 extra categorical covariates and 0 extra
         continuous covariates.                                                              
INFO     Please do not further modify adata until model is trained.                          


### 14.11.2021 Running scVI after:

- removing soupy genes as per LF approach (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell)

In [13]:
# this one is without soupy gene removal

models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

n_latent_values = [9]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 9


In [14]:
# without soupy gene filtering and with CC-assoc gene filtering

latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211123_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_NK_and_T_compartments_clean_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 9
Epoch 169/169: 100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 169/169 [09:16<00:00,  3.29s/it, loss=590, v_num=1]


# Running on Myeloid compartment (after all cleanup, for zoomed in visualisation in Fig.1B)


Subsetted by unbiased clusteing of the manifold with all cell states as calculated above with n_latent=

In [15]:
save_path = '/lustre/scratch117/cellgen/team292/aa22/adata_objects/202111_MFI_sc_sn_new_scVI_analysis/'

# Loading object with raw counts, filtered cells and genes object
# before any doublet exclusion
adata = sc.read(save_path + 'adata_raw_filtered.h5ad')


In [16]:
# read in final annotations
final_annot = pd.read_csv(save_path + 'final_annotation_all_cells_and_nulcei_20211119.csv', index_col=0)

# subset to only cells in final manifold
adata = adata[final_annot.index,:].copy()
adata.obs['cell_type'] = final_annot.loc[adata.obs_names,'cell_type']
# subsetting to only NK and T cells
adata = adata[adata.obs['cell_type'].isin(['dM1','dM2','M3','MO','HOFB','Granulocytes','dDC','DC','B_cells','Plasma'])]

In [17]:
# excluding soupy genes as per notebook M2

# gene stats for cells
gene_stats_sc = pd.read_csv(save_path + 'gene_filter_cells_upd_20211111.csv', index_col=0)

# gene stats for nuclei
gene_stats_sn = pd.read_csv(save_path + 'gene_filter_nuclei_upd_20211111.csv', index_col=0)

genes2keep_sc = list(gene_stats_sc[gene_stats_sc['Selected'] == True].index)
genes2keep_sn = list(gene_stats_sn[gene_stats_sn['Selected'] == True].index)

# overlap
genes2keep = list(set(genes2keep_sc) & set(genes2keep_sn))

print(len(genes2keep))

adata = adata[:,list(set(genes2keep) & set(adata.var_names))].copy()
adata

# cell cycle related - no need to, seems like all of those have been removed by soupy gene filter
#cleaned_up_genes_cc = pd.read_csv(save_path + '', index_col=0)

7849


AnnData object with n_obs × n_vars = 41017 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'cell_type'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feat

In [18]:
adata

AnnData object with n_obs × n_vars = 41017 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'cell_type'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feat

In [19]:
# optimal n_PCs = 10 here

In [20]:
# do some basic preprocessing
adata.layers["raw_counts"] = adata.X.copy() # preserve counts
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
adata.raw = adata.copy()

In [21]:
adata

AnnData object with n_obs × n_vars = 41017 × 7848
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'cell_type'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feat

In [22]:
# here we subset to HVGs, not accounting for sample batch here - it breaks the HVG finding (not enough batch representation?)
sc.pp.highly_variable_genes(adata, min_mean=0.0125, max_mean=3, min_disp=0.5,
                           subset=True)

In [23]:
adata

AnnData object with n_obs × n_vars = 41017 × 2062
    obs: 'n_genes', 'sample', 'technology', 'tissue', 'dev_age', 'donor', 'dataset', 'run', 'number_of_individuals_multiplexed', 'batch', 'percent_mito', 'n_counts', 'scrublet_score', 'scrublet_cluster_score', 'bh_pval', 'is_doublet', 'cell_type'
    var: 'gene_ids-0', 'feature_types-0', 'genome-0', 'n_cells-0', 'gene_ids-1', 'feature_types-1', 'genome-1', 'n_cells-1', 'gene_ids-10', 'feature_types-10', 'genome-10', 'n_cells-10', 'gene_ids-11', 'feature_types-11', 'genome-11', 'n_cells-11', 'gene_ids-12', 'feature_types-12', 'genome-12', 'n_cells-12', 'gene_ids-13', 'feature_types-13', 'genome-13', 'n_cells-13', 'gene_ids-14', 'feature_types-14', 'genome-14', 'n_cells-14', 'gene_ids-15', 'feature_types-15', 'genome-15', 'n_cells-15', 'gene_ids-16', 'feature_types-16', 'genome-16', 'n_cells-16', 'gene_ids-17', 'feature_types-17', 'genome-17', 'n_cells-17', 'gene_ids-18', 'feature_types-18', 'genome-18', 'n_cells-18', 'gene_ids-19', 'feat

#### Here you can specify your covariates you want to correct for (categorical or continuous)

In [24]:
scvi.data.setup_anndata(
    adata,
    layer="raw_counts",
    categorical_covariate_keys=["sample"],
    #continuous_covariate_keys=[""] # could try and regress n_genes in the future? not for now
)

INFO     No batch_key inputted, assuming all cells are same batch                            
INFO     No label_key inputted, assuming all cells have same label                           
INFO     Using data from adata.layers["raw_counts"]                                          
INFO     Computing library size prior per batch                                              
INFO     Successfully registered anndata object containing 41017 cells, 2062 vars, 1 batches,
         1 labels, and 0 proteins. Also registered 1 extra categorical covariates and 0 extra
         continuous covariates.                                                              
INFO     Please do not further modify adata until model is trained.                          


### 14.11.2021 Running scVI after:

- removing soupy genes as per LF approach (calculated in M2 notebook)
- exclusion of all doublets (scrublet and souporcell)

In [25]:
# this one is without soupy gene removal

models_n_layers_1 = {}

models_n_layers_2 = {}

models_n_layers_3 = {}

n_latent_values = [10]

for n_latent_value in n_latent_values:
    print('n_latent_value', n_latent_value)
    models_n_layers_1[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 1)
    models_n_layers_2[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 2)
    models_n_layers_3[n_latent_value] = scvi.model.SCVI(adata, n_latent = n_latent_value,
                                  # n_layers is by default 1 but using more may help with more difficult cases?
                                  n_layers = 3)

n_latent_value 10


In [26]:
# without soupy gene filtering and with CC-assoc gene filtering

latent_representations_n_layers_3 = {}

for n_latent_value in n_latent_values:
    print('training model for n_latent_value:', n_latent_value)
    models_n_layers_3[n_latent_value].train()
    
    # get latent representation as a dataframe
    latent_representations_n_layers_3[n_latent_value] = models_n_layers_3[n_latent_value].get_latent_representation()
    
    # add it to the adata object
    adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"] = latent_representations_n_layers_3[n_latent_value]
    curr_df = pd.DataFrame(adata.obsm["X_scVI_n_latent_" + str(n_latent_value) + "_n_layers_3"])
    
    # save the latent representation
    curr_df.to_csv('./results/20211123_obsm_with_scVI_latent_representation_n_' + str(n_latent_value) + '_after_all_doublet_exclusion_by_sample_Myeloid_compartment_clean_n_layers_3.csv')
    

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


training model for n_latent_value: 10
Epoch 195/195: 100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 195/195 [09:03<00:00,  2.79s/it, loss=413, v_num=1]
